In [1]:
nb_epochs = 2000
#nb_epochs = 1

In [2]:
#FCN-I

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function


from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
#    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('relu')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
#    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
#    conv2 = keras.layers.Activation('relu')(conv2)
    
#    drop_out = Dropout(0.2)(conv2)
#    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
#    conv3 = keras.layers.Activation('relu')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv1)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
    hist1 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
    log1 = pd.DataFrame(hist1.history)
 #   print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_modle1
fcn_model1 = keras.models.load_model(model_h5_file)


A module that was compiled using NumPy 1.x cannot be run in
NumPy 2.0.2 as it may crash. To support both 1.x and 2.x
versions of NumPy, modules must be compiled with NumPy 2.0.
Some module may need to rebuild instead e.g. with 'pybind11>=2.12'.

If you are a user of the module, the easiest solution will be to
downgrade to 'numpy<2' or try to upgrade the affected module.
We expect that some modules will need time to support NumPy 2.

Traceback (most recent call last):  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 197, in _run_module_as_main
    return _run_code(code, main_globals, None,
  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 87, in _run_code
    exec(code, run_globals)
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipykernel_launcher.py", line 17, in <module>
    app.launch_new_instance()
  File "C:\Users\KJH\anaconda3\lib\site-packages\traitlets\config\application.py", line 846, in launch_instance
    app.start()
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipyke

AttributeError: _ARRAY_API not found


A module that was compiled using NumPy 1.x cannot be run in
NumPy 2.0.2 as it may crash. To support both 1.x and 2.x
versions of NumPy, modules must be compiled with NumPy 2.0.
Some module may need to rebuild instead e.g. with 'pybind11>=2.12'.

If you are a user of the module, the easiest solution will be to
downgrade to 'numpy<2' or try to upgrade the affected module.
We expect that some modules will need time to support NumPy 2.

Traceback (most recent call last):  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 197, in _run_module_as_main
    return _run_code(code, main_globals, None,
  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 87, in _run_code
    exec(code, run_globals)
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipykernel_launcher.py", line 17, in <module>
    app.launch_new_instance()
  File "C:\Users\KJH\anaconda3\lib\site-packages\traitlets\config\application.py", line 846, in launch_instance
    app.start()
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipyke

AttributeError: _ARRAY_API not found


A module that was compiled using NumPy 1.x cannot be run in
NumPy 2.0.2 as it may crash. To support both 1.x and 2.x
versions of NumPy, modules must be compiled with NumPy 2.0.
Some module may need to rebuild instead e.g. with 'pybind11>=2.12'.

If you are a user of the module, the easiest solution will be to
downgrade to 'numpy<2' or try to upgrade the affected module.
We expect that some modules will need time to support NumPy 2.

Traceback (most recent call last):  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 197, in _run_module_as_main
    return _run_code(code, main_globals, None,
  File "C:\Users\KJH\anaconda3\lib\runpy.py", line 87, in _run_code
    exec(code, run_globals)
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipykernel_launcher.py", line 17, in <module>
    app.launch_new_instance()
  File "C:\Users\KJH\anaconda3\lib\site-packages\traitlets\config\application.py", line 846, in launch_instance
    app.start()
  File "C:\Users\KJH\anaconda3\lib\site-packages\ipyke

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7017 - loss: 0.5544 - val_accuracy: 0.7096 - val_loss: 0.6900 - learning_rate: 1.0000e-04
Epoch 1821/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.7193 - loss: 0.5361 - val_accuracy: 0.7096 - val_loss: 0.6845 - learning_rate: 1.0000e-04
Epoch 1822/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - accuracy: 0.7276 - loss: 0.5361 - val_accuracy: 0.7113 - val_loss: 0.6873 - learning_rate: 1.0000e-04
Epoch 1823/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7027 - loss: 0.5672 - val_accuracy: 0.7096 - val_loss: 0.6839 - learning_rate: 1.0000e-04
Epoch 1824/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7358 - loss: 0.5496 - val_accuracy: 0.7113 - val_loss: 0.6838 - learning_rate: 1.0000e-04
Epoch 1825/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7133 - loss: 0.5643 - val_accuracy: 0.7064 - val_loss: 0.6834 - learning_rate: 1.0000e-04
Epoch 1826/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - ac

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6822 - loss: 0.5929 - val_accuracy: 0.7113 - val_loss: 0.6853 - learning_rate: 1.0000e-04
Epoch 1863/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7421 - loss: 0.5263 - val_accuracy: 0.6998 - val_loss: 0.6996 - learning_rate: 1.0000e-04
Epoch 1864/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6918 - loss: 0.6052 - val_accuracy: 0.7080 - val_loss: 0.6838 - learning_rate: 1.0000e-04
Epoch 1865/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - accuracy: 0.7152 - loss: 0.5501 - val_accuracy: 0.7064 - val_loss: 0.6845 - learning_rate: 1.0000e-04
Epoch 1866/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6934 - loss: 0.5631 - val_accuracy: 0.7047 - val_loss: 0.6863 - learning_rate: 1.0000e-04
Epoch 1867/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7211 - loss: 0.5593 - val_accuracy: 0.7015 - val_loss: 0.7013 - learning_rate: 1.0000e-04
Epoch 1868/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - ac

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7050 - loss: 0.5475 - val_accuracy: 0.7113 - val_loss: 0.6842 - learning_rate: 1.0000e-04
Epoch 1905/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7023 - loss: 0.5708 - val_accuracy: 0.7047 - val_loss: 0.6925 - learning_rate: 1.0000e-04
Epoch 1906/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7234 - loss: 0.5471 - val_accuracy: 0.7096 - val_loss: 0.6900 - learning_rate: 1.0000e-04
Epoch 1907/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6853 - loss: 0.5970 - val_accuracy: 0.7080 - val_loss: 0.6840 - learning_rate: 1.0000e-04
Epoch 1908/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7227 - loss: 0.5475 - val_accuracy: 0.7064 - val_loss: 0.6851 - learning_rate: 1.0000e-04
Epoch 1909/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7260 - loss: 0.5559 - val_accuracy: 0.7064 - val_loss: 0.6850 - learning_rate: 1.0000e-04
Epoch 1910/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - acc

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7113 - loss: 0.5719 - val_accuracy: 0.7096 - val_loss: 0.6889 - learning_rate: 1.0000e-04
Epoch 1947/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6730 - loss: 0.5912 - val_accuracy: 0.7047 - val_loss: 0.7297 - learning_rate: 1.0000e-04
Epoch 1948/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6946 - loss: 0.5626 - val_accuracy: 0.7064 - val_loss: 0.6862 - learning_rate: 1.0000e-04
Epoch 1949/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6889 - loss: 0.5818 - val_accuracy: 0.7064 - val_loss: 0.7162 - learning_rate: 1.0000e-04
Epoch 1950/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7265 - loss: 0.5464 - val_accuracy: 0.7080 - val_loss: 0.6847 - learning_rate: 1.0000e-04
Epoch 1951/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7034 - loss: 0.5777 - val_accuracy: 0.6966 - val_loss: 0.6980 - learning_rate: 1.0000e-04
Epoch 1952/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - acc

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7144 - loss: 0.5767 - val_accuracy: 0.6998 - val_loss: 0.7049 - learning_rate: 1.0000e-04
Epoch 1989/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7049 - loss: 0.5487 - val_accuracy: 0.7047 - val_loss: 0.6849 - learning_rate: 1.0000e-04
Epoch 1990/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7457 - loss: 0.5229 - val_accuracy: 0.7064 - val_loss: 0.6863 - learning_rate: 1.0000e-04
Epoch 1991/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7179 - loss: 0.5508 - val_accuracy: 0.7096 - val_loss: 0.6883 - learning_rate: 1.0000e-04
Epoch 1992/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6866 - loss: 0.5783 - val_accuracy: 0.7113 - val_loss: 0.6875 - learning_rate: 1.0000e-04
Epoch 1993/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7040 - loss: 0.5607 - val_accuracy: 0.7047 - val_loss: 0.6858 - learning_rate: 1.0000e-04
Epoch 1994/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 8ms/step - a

In [3]:
#FCN-II

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
#    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('relu')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('relu')(conv2)
    
#    drop_out = Dropout(0.2)(conv2)
#    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
#    conv3 = keras.layers.Activation('relu')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv2)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist2 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log2 = pd.DataFrame(hist2.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_modle2
fcn_model2 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 4s 35ms/step - accuracy: 0.4979 - loss: 0.6922 - val_accuracy: 0.6199 - val_loss: 2.7115 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.5699 - loss: 0.6993 - val_accuracy: 0.6199 - val_loss: 1.0355 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.5911 - loss: 0.6800 - val_accuracy: 0.6199 - val_loss: 1.0127 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.5913 - loss: 0.6757 - val_accuracy: 0.6199 - val_loss: 0.8904 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.5564 - loss: 0.6805 - val_accuracy: 0.6199 - val_loss: 0.9012 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.5726 - loss: 0.6742 - val_accuracy: 0.6199 - val_loss: 1.2525 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.5418 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7171 - loss: 0.5886 - val_accuracy: 0.6623 - val_loss: 0.8192 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 17ms/step - accuracy: 0.6632 - loss: 0.5919 - val_accuracy: 0.6917 - val_loss: 0.6606 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7269 - loss: 0.5562 - val_accuracy: 0.6427 - val_loss: 1.1858 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7042 - loss: 0.5869 - val_accuracy: 0.6868 - val_loss: 0.6430 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7186 - loss: 0.5775 - val_accuracy: 0.6607 - val_loss: 0.8729 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6998 - loss: 0.5646 - val_accuracy: 0.6411 - val_loss: 1.4666 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7289 - loss: 0.5599 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6983 - loss: 0.5915 - val_accuracy: 0.6362 - val_loss: 1.7565 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7097 - loss: 0.5782 - val_accuracy: 0.6493 - val_loss: 1.1659 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7012 - loss: 0.5842 - val_accuracy: 0.6688 - val_loss: 0.8079 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7190 - loss: 0.5563 - val_accuracy: 0.6476 - val_loss: 1.4685 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7088 - loss: 0.5658 - val_accuracy: 0.6623 - val_loss: 0.9408 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7119 - loss: 0.5659 - val_accuracy: 0.6982 - val_loss: 0.7341 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7037 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7315 - loss: 0.5504 - val_accuracy: 0.7015 - val_loss: 0.6845 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7238 - loss: 0.5483 - val_accuracy: 0.6900 - val_loss: 0.7694 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7551 - loss: 0.5467 - val_accuracy: 0.7015 - val_loss: 0.6710 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6975 - loss: 0.5677 - val_accuracy: 0.6884 - val_loss: 0.8140 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6799 - loss: 0.5766 - val_accuracy: 0.6917 - val_loss: 0.7272 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7161 - loss: 0.5364 - val_accuracy: 0.6607 - val_loss: 1.2227 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7114 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7470 - loss: 0.5354 - val_accuracy: 0.4976 - val_loss: 1.4472 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7145 - loss: 0.5177 - val_accuracy: 0.5334 - val_loss: 1.1953 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7317 - loss: 0.5349 - val_accuracy: 0.7129 - val_loss: 0.7015 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7218 - loss: 0.5320 - val_accuracy: 0.7015 - val_loss: 0.6986 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6840 - loss: 0.5679 - val_accuracy: 0.4878 - val_loss: 1.4206 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7150 - loss: 0.5408 - val_accuracy: 0.6884 - val_loss: 0.7323 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7517 - loss: 0.5

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9957 - loss: 0.0525 - val_accuracy: 0.6770 - val_loss: 12.4101 - learning_rate: 5.0000e-04
Epoch 1803/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9895 - loss: 0.0404 - val_accuracy: 0.6721 - val_loss: 13.1496 - learning_rate: 5.0000e-04
Epoch 1804/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.9959 - loss: 0.0349 - val_accuracy: 0.6737 - val_loss: 11.7403 - learning_rate: 5.0000e-04
Epoch 1805/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9916 - loss: 0.0372 - val_accuracy: 0.6737 - val_loss: 12.3168 - learning_rate: 5.0000e-04
Epoch 1806/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9906 - loss: 0.0413 - val_accuracy: 0.6786 - val_loss: 11.8297 - learning_rate: 5.0000e-04
Epoch 1807/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.9855 - loss: 0.0424 - val_accuracy: 0.6786 - val_loss: 12.2273 - learning_rate: 5.0000e-04
Epoch 1808/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9935 - loss: 0.0317 - val_accuracy: 0.6705 - val_loss: 11.8332 - learning_rate: 5.0000e-04
Epoch 1845/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9943 - loss: 0.0433 - val_accuracy: 0.6509 - val_loss: 12.2045 - learning_rate: 5.0000e-04
Epoch 1846/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9977 - loss: 0.0337 - val_accuracy: 0.6754 - val_loss: 11.7261 - learning_rate: 5.0000e-04
Epoch 1847/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9942 - loss: 0.0402 - val_accuracy: 0.6803 - val_loss: 12.0773 - learning_rate: 5.0000e-04
Epoch 1848/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9956 - loss: 0.0332 - val_accuracy: 0.6623 - val_loss: 11.9554 - learning_rate: 5.0000e-04
Epoch 1849/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.9973 - loss: 0.0393 - val_accuracy: 0.6737 - val_loss: 11.9186 - learning_rate: 5.0000e-04
Epoch 1850/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.9955 - loss: 0.0386 - val_accuracy: 0.6411 - val_loss: 12.6278 - learning_rate: 5.0000e-04
Epoch 1887/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9936 - loss: 0.0353 - val_accuracy: 0.6639 - val_loss: 12.3624 - learning_rate: 5.0000e-04
Epoch 1888/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9954 - loss: 0.0399 - val_accuracy: 0.6330 - val_loss: 12.9306 - learning_rate: 5.0000e-04
Epoch 1889/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9935 - loss: 0.0340 - val_accuracy: 0.6036 - val_loss: 13.5872 - learning_rate: 5.0000e-04
Epoch 1890/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.9936 - loss: 0.0457 - val_accuracy: 0.6737 - val_loss: 13.5722 - learning_rate: 5.0000e-04
Epoch 1891/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 26ms/step - accuracy: 0.9940 - loss: 0.0345 - val_accuracy: 0.6770 - val_loss: 12.1722 - learning_rate: 5.0000e-04
Epoch 1892/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9973 - loss: 0.0288 - val_accuracy: 0.6623 - val_loss: 12.5331 - learning_rate: 5.0000e-04
Epoch 1929/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9936 - loss: 0.0348 - val_accuracy: 0.6672 - val_loss: 12.4439 - learning_rate: 5.0000e-04
Epoch 1930/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9985 - loss: 0.0304 - val_accuracy: 0.6737 - val_loss: 12.1919 - learning_rate: 5.0000e-04
Epoch 1931/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9946 - loss: 0.0305 - val_accuracy: 0.6705 - val_loss: 12.1120 - learning_rate: 5.0000e-04
Epoch 1932/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9950 - loss: 0.0375 - val_accuracy: 0.6591 - val_loss: 12.5432 - learning_rate: 5.0000e-04
Epoch 1933/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9990 - loss: 0.0306 - val_accuracy: 0.6688 - val_loss: 12.1227 - learning_rate: 5.0000e-04
Epoch 1934/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.9910 - loss: 0.0441 - val_accuracy: 0.6509 - val_loss: 12.8012 - learning_rate: 5.0000e-04
Epoch 1971/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.9988 - loss: 0.0299 - val_accuracy: 0.6525 - val_loss: 12.6835 - learning_rate: 5.0000e-04
Epoch 1972/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.9958 - loss: 0.0287 - val_accuracy: 0.6607 - val_loss: 12.7599 - learning_rate: 5.0000e-04
Epoch 1973/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9901 - loss: 0.0343 - val_accuracy: 0.6297 - val_loss: 13.6904 - learning_rate: 5.0000e-04
Epoch 1974/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9933 - loss: 0.0292 - val_accuracy: 0.6362 - val_loss: 13.0869 - learning_rate: 5.0000e-04
Epoch 1975/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9996 - loss: 0.0267 - val_accuracy: 0.6330 - val_loss: 13.5296 - learning_rate: 5.0000e-04
Epoch 1976/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms

In [4]:
#FCN-III

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
#    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('relu')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('relu')(conv2)
    

    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.Activation('relu')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv3)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist3 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log3 = pd.DataFrame(hist3.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_modle3
fcn_model3 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 6s 54ms/step - accuracy: 0.5382 - loss: 0.6930 - val_accuracy: 0.6199 - val_loss: 0.9676 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.5526 - loss: 0.6875 - val_accuracy: 0.6199 - val_loss: 1.3505 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.5467 - loss: 0.6905 - val_accuracy: 0.6199 - val_loss: 1.0695 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.5832 - loss: 0.6785 - val_accuracy: 0.6199 - val_loss: 0.7457 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.5672 - loss: 0.6807 - val_accuracy: 0.6199 - val_loss: 0.6716 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.5496 - loss: 0.6881 - val_accuracy: 0.6199 - val_loss: 0.6770 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.5911 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6695 - loss: 0.6017 - val_accuracy: 0.6688 - val_loss: 0.7334 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7164 - loss: 0.5735 - val_accuracy: 0.5563 - val_loss: 0.9406 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6800 - loss: 0.5741 - val_accuracy: 0.6362 - val_loss: 1.3805 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7163 - loss: 0.5582 - val_accuracy: 0.6542 - val_loss: 0.9239 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7379 - loss: 0.5593 - val_accuracy: 0.6558 - val_loss: 0.8399 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.6998 - loss: 0.5554 - val_accuracy: 0.6770 - val_loss: 0.8090 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7076 - loss: 0.5670 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7386 - loss: 0.5325 - val_accuracy: 0.7015 - val_loss: 0.8539 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7556 - loss: 0.5148 - val_accuracy: 0.6574 - val_loss: 1.4962 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7465 - loss: 0.4962 - val_accuracy: 0.6737 - val_loss: 0.9448 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7116 - loss: 0.5487 - val_accuracy: 0.6656 - val_loss: 1.3447 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7137 - loss: 0.5313 - val_accuracy: 0.4633 - val_loss: 3.6070 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7250 - loss: 0.5121 - val_accuracy: 0.6770 - val_loss: 0.9932 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7602 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7755 - loss: 0.4440 - val_accuracy: 0.6688 - val_loss: 1.0411 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7934 - loss: 0.4356 - val_accuracy: 0.4584 - val_loss: 3.8772 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7629 - loss: 0.4556 - val_accuracy: 0.7047 - val_loss: 1.1147 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7626 - loss: 0.4641 - val_accuracy: 0.4388 - val_loss: 5.0413 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7798 - loss: 0.4621 - val_accuracy: 0.4617 - val_loss: 3.5690 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7725 - loss: 0.4464 - val_accuracy: 0.4519 - val_loss: 4.6264 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7971 - loss: 0.4

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.8090 - loss: 0.3763 - val_accuracy: 0.4144 - val_loss: 11.8550 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.8304 - loss: 0.3849 - val_accuracy: 0.4290 - val_loss: 8.9977 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7861 - loss: 0.3946 - val_accuracy: 0.4111 - val_loss: 10.7423 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7964 - loss: 0.4083 - val_accuracy: 0.4372 - val_loss: 7.8468 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7990 - loss: 0.4116 - val_accuracy: 0.4339 - val_loss: 5.8406 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.8235 - loss: 0.3581 - val_accuracy: 0.4323 - val_loss: 8.6317 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.8112 - loss: 0

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 2.1567e-04 - val_accuracy: 0.4682 - val_loss: 76.3953 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 1.6956e-04 - val_accuracy: 0.4698 - val_loss: 76.8894 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 1.0000 - loss: 1.7014e-04 - val_accuracy: 0.4698 - val_loss: 76.8850 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 1.0000 - loss: 1.7889e-04 - val_accuracy: 0.4698 - val_loss: 77.1936 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 2.3710e-04 - val_accuracy: 0.4666 - val_loss: 77.6411 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 2.3051e-04 - val_accuracy: 0.4682 - val_loss: 76.8329 - learning_rate: 1.0000e-04
Epoch 1819/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 1.6130e-04 - val_accuracy: 0.4486 - val_loss: 85.4705 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 2.0029e-04 - val_accuracy: 0.4470 - val_loss: 85.7668 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 1.4595e-04 - val_accuracy: 0.4470 - val_loss: 86.3787 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 1.0000 - loss: 2.6002e-04 - val_accuracy: 0.4470 - val_loss: 86.4770 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 1.6338e-04 - val_accuracy: 0.4454 - val_loss: 86.9628 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 1.0000 - loss: 1.6668e-04 - val_accuracy: 0.4470 - val_loss: 86.8992 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 1.4439e-04 - val_accuracy: 0.4470 - val_loss: 89.0175 - learning_rate: 1.0000e-04
Epoch 1896/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 2.1011e-04 - val_accuracy: 0.4454 - val_loss: 89.1164 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 1.7997e-04 - val_accuracy: 0.4454 - val_loss: 89.2910 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 1.6982e-04 - val_accuracy: 0.4454 - val_loss: 88.9464 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 1.9512e-04 - val_accuracy: 0.4405 - val_loss: 90.2540 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 2.0773e-04 - val_accuracy: 0.4454 - val_loss: 88.7198 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 1.3665e-04 - val_accuracy: 0.4470 - val_loss: 88.6903 - learning_rate: 1.0000e-04
Epoch 1937/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 1.0000 - loss: 1.7081e-04 - val_accuracy: 0.4454 - val_loss: 88.2357 - learning_rate: 1.0000e-04
Epoch 1938/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 1.6481e-04 - val_accuracy: 0.4454 - val_loss: 88.5956 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 2.1938e-04 - val_accuracy: 0.4486 - val_loss: 88.6777 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 1.0000 - loss: 1.7909e-04 - val_accuracy: 0.4535 - val_loss: 87.2280 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 2.2702e-04 - val_accuracy: 0.4486 - val_loss: 88.5663 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 1.0000 - loss: 1.1313e-04 - val_accuracy: 0.4405 - val_loss: 90.2002 - learning_rate: 1.0000e-04
Epoch 1978/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 1.6827e-04 - val_accuracy: 0.4405 - val_loss: 90.2348 - learning_rate: 1.0000e-04
Epoch 1979/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 1.2176e-04 - val_accuracy: 0.4388 - val_loss: 90.7441 - learning_rate: 1.0000e-04
Epoch 1980/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 1.1278e-04 - val_accuracy: 0.4388 - val_loss: 90.2151 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 1.1632e-04 - val_accuracy: 0.4388 - val_loss: 91.0208 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 1.1819e-04 - val_accuracy: 0.4388 - val_loss: 91.1150 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━

In [5]:
#FCN-IV

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
#    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('relu')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('relu')(conv2)
    

    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.Activation('relu')(conv3)


    conv4 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv3)
#    conv4 = keras.layers.BatchNormalization()(conv4)
    conv4 = keras.layers.Activation('relu')(conv4)
    
    full = keras.layers.GlobalAveragePooling2D()(conv4)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist4 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log4 = pd.DataFrame(hist4.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_model4
fcn_model4 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 8s 61ms/step - accuracy: 0.5262 - loss: 0.6970 - val_accuracy: 0.6199 - val_loss: 0.6868 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.5760 - loss: 0.6832 - val_accuracy: 0.6199 - val_loss: 1.0299 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.5671 - loss: 0.6844 - val_accuracy: 0.6199 - val_loss: 0.7783 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.5888 - loss: 0.6790 - val_accuracy: 0.6199 - val_loss: 0.7101 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.5553 - loss: 0.6855 - val_accuracy: 0.6199 - val_loss: 1.1240 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 41ms/step - accuracy: 0.5403 - loss: 0.6870 - val_accuracy: 0.6199 - val_loss: 0.8770 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.5867 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.6948 - loss: 0.5903 - val_accuracy: 0.6591 - val_loss: 0.8258 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 44ms/step - accuracy: 0.7170 - loss: 0.5763 - val_accuracy: 0.6411 - val_loss: 1.4230 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.7274 - loss: 0.5645 - val_accuracy: 0.6574 - val_loss: 1.0173 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 38ms/step - accuracy: 0.7205 - loss: 0.5630 - val_accuracy: 0.6395 - val_loss: 1.5951 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7096 - loss: 0.5461 - val_accuracy: 0.6868 - val_loss: 0.7522 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.7349 - loss: 0.5417 - val_accuracy: 0.6378 - val_loss: 1.4956 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.7103 - loss: 0.5705 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7373 - loss: 0.5237 - val_accuracy: 0.6966 - val_loss: 0.9066 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7239 - loss: 0.5517 - val_accuracy: 0.6868 - val_loss: 0.9540 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.7698 - loss: 0.5221 - val_accuracy: 0.5726 - val_loss: 1.9101 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 39ms/step - accuracy: 0.7136 - loss: 0.5698 - val_accuracy: 0.6558 - val_loss: 1.9234 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7612 - loss: 0.5133 - val_accuracy: 0.6917 - val_loss: 1.0239 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7295 - loss: 0.5373 - val_accuracy: 0.6835 - val_loss: 1.0784 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.7341 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7673 - loss: 0.4870 - val_accuracy: 0.4747 - val_loss: 5.6629 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.7523 - loss: 0.4851 - val_accuracy: 0.4943 - val_loss: 4.0870 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.7695 - loss: 0.4658 - val_accuracy: 0.5498 - val_loss: 2.4761 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7617 - loss: 0.4783 - val_accuracy: 0.4845 - val_loss: 4.7206 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7956 - loss: 0.4436 - val_accuracy: 0.6998 - val_loss: 0.9737 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.7581 - loss: 0.4911 - val_accuracy: 0.6362 - val_loss: 1.5441 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7673 - loss: 0.4

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.8147 - loss: 0.4025 - val_accuracy: 0.4111 - val_loss: 17.0519 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 39ms/step - accuracy: 0.8286 - loss: 0.3666 - val_accuracy: 0.3964 - val_loss: 22.5462 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.8234 - loss: 0.3608 - val_accuracy: 0.3948 - val_loss: 21.8017 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.8369 - loss: 0.3627 - val_accuracy: 0.4274 - val_loss: 9.2601 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.8109 - loss: 0.3883 - val_accuracy: 0.5057 - val_loss: 2.7061 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.7950 - loss: 0.4067 - val_accuracy: 0.4649 - val_loss: 4.6265 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.7972 - loss: 

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 1.0125e-04 - val_accuracy: 0.3883 - val_loss: 176.0848 - learning_rate: 1.0000e-04
Epoch 1803/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 6.9056e-05 - val_accuracy: 0.3883 - val_loss: 176.0369 - learning_rate: 1.0000e-04
Epoch 1804/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 1.0000 - loss: 4.4902e-05 - val_accuracy: 0.3883 - val_loss: 176.0080 - learning_rate: 1.0000e-04
Epoch 1805/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 5.0792e-05 - val_accuracy: 0.3883 - val_loss: 175.8126 - learning_rate: 1.0000e-04
Epoch 1806/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 5.9862e-05 - val_accuracy: 0.3883 - val_loss: 175.7696 - learning_rate: 1.0000e-04
Epoch 1807/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 1.0000 - loss: 4.5748e-05 - val_accuracy: 0.3883 - val_loss: 175.6112 - learning_rate: 1.0000e-04
Epoch 1808/2000
37/3

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 2.5527e-05 - val_accuracy: 0.3883 - val_loss: 172.9664 - learning_rate: 1.0000e-04
Epoch 1844/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 1.0000 - loss: 3.4949e-05 - val_accuracy: 0.3883 - val_loss: 172.8315 - learning_rate: 1.0000e-04
Epoch 1845/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 2.2286e-05 - val_accuracy: 0.3883 - val_loss: 172.8203 - learning_rate: 1.0000e-04
Epoch 1846/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 1.0000 - loss: 3.9448e-05 - val_accuracy: 0.3883 - val_loss: 172.9612 - learning_rate: 1.0000e-04
Epoch 1847/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 3.6788e-05 - val_accuracy: 0.3883 - val_loss: 173.0789 - learning_rate: 1.0000e-04
Epoch 1848/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 4.1736e-05 - val_accuracy: 0.3883 - val_loss: 173.0257 - learning_rate: 1.0000e-04
Epoch 1849/2000
37/3

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 1.9365e-05 - val_accuracy: 0.3899 - val_loss: 172.9453 - learning_rate: 1.0000e-04
Epoch 1885/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 1.0000 - loss: 2.0959e-05 - val_accuracy: 0.3899 - val_loss: 172.6915 - learning_rate: 1.0000e-04
Epoch 1886/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 3.4470e-05 - val_accuracy: 0.3899 - val_loss: 172.8877 - learning_rate: 1.0000e-04
Epoch 1887/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 2.5202e-05 - val_accuracy: 0.3899 - val_loss: 172.8930 - learning_rate: 1.0000e-04
Epoch 1888/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 2.7759e-05 - val_accuracy: 0.3899 - val_loss: 172.8697 - learning_rate: 1.0000e-04
Epoch 1889/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 2.5525e-05 - val_accuracy: 0.3899 - val_loss: 173.0299 - learning_rate: 1.0000e-04
Epoch 1890/2000
37/3

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 1.0000 - loss: 1.1456e-04 - val_accuracy: 0.4078 - val_loss: 161.8613 - learning_rate: 1.0000e-04
Epoch 1926/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 7.4086e-05 - val_accuracy: 0.4078 - val_loss: 162.2108 - learning_rate: 1.0000e-04
Epoch 1927/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 6.9623e-05 - val_accuracy: 0.4078 - val_loss: 162.6129 - learning_rate: 1.0000e-04
Epoch 1928/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 8.2073e-05 - val_accuracy: 0.4062 - val_loss: 162.9511 - learning_rate: 1.0000e-04
Epoch 1929/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 1.0553e-04 - val_accuracy: 0.4046 - val_loss: 163.2682 - learning_rate: 1.0000e-04
Epoch 1930/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 6.3791e-05 - val_accuracy: 0.4046 - val_loss: 163.4945 - learning_rate: 1.0000e-04
Epoch 1931/2000
37/3

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 2.5270e-05 - val_accuracy: 0.3997 - val_loss: 167.5947 - learning_rate: 1.0000e-04
Epoch 1967/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 3.7581e-05 - val_accuracy: 0.3997 - val_loss: 167.6045 - learning_rate: 1.0000e-04
Epoch 1968/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 2.2498e-05 - val_accuracy: 0.3997 - val_loss: 167.7263 - learning_rate: 1.0000e-04
Epoch 1969/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 1.0000 - loss: 4.6257e-05 - val_accuracy: 0.3997 - val_loss: 167.6874 - learning_rate: 1.0000e-04
Epoch 1970/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 1.0000 - loss: 4.3116e-05 - val_accuracy: 0.3997 - val_loss: 167.7670 - learning_rate: 1.0000e-04
Epoch 1971/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 4.5399e-05 - val_accuracy: 0.3997 - val_loss: 167.7499 - learning_rate: 1.0000e-04
Epoch 1972/2000
37/3

In [6]:
#FCN-V

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('relu')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
#    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
#    conv2 = keras.layers.Activation('relu')(conv2)
    
#    drop_out = Dropout(0.2)(conv2)
#    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
#    conv3 = keras.layers.Activation('relu')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv1)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist5 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
    log5 = pd.DataFrame(hist5.history)
 #   print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_model5
fcn_model5 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 3s 22ms/step - accuracy: 0.4965 - loss: 0.7472 - val_accuracy: 0.6199 - val_loss: 0.8875 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.5438 - loss: 0.7080 - val_accuracy: 0.6199 - val_loss: 0.8318 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.5951 - loss: 0.6664 - val_accuracy: 0.6199 - val_loss: 0.8676 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6190 - loss: 0.6739 - val_accuracy: 0.6199 - val_loss: 0.8667 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6279 - loss: 0.6526 - val_accuracy: 0.6199 - val_loss: 1.0019 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6318 - loss: 0.6465 - val_accuracy: 0.6199 - val_loss: 1.3044 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6417 - loss: 0.63

Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6662 - loss: 0.6183 - val_accuracy: 0.6199 - val_loss: 3.3510 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6590 - loss: 0.6134 - val_accuracy: 0.6558 - val_loss: 0.7817 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6935 - loss: 0.6015 - val_accuracy: 0.6297 - val_loss: 1.6024 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6619 - loss: 0.6158 - val_accuracy: 0.6411 - val_loss: 1.1034 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6702 - loss: 0.5961 - val_accuracy: 0.7129 - val_loss: 0.6141 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.6792 - loss: 0.6115 - val_accuracy: 0.6215 - val_loss: 2.5259 - learning_rate: 0.0010
Epoch 51/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6944 - loss

Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - accuracy: 0.6821 - loss: 0.5964 - val_accuracy: 0.4959 - val_loss: 1.1167 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6646 - loss: 0.5895 - val_accuracy: 0.6542 - val_loss: 0.7156 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7034 - loss: 0.5841 - val_accuracy: 0.6281 - val_loss: 2.1982 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6790 - loss: 0.5789 - val_accuracy: 0.6656 - val_loss: 0.7369 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6999 - loss: 0.5789 - val_accuracy: 0.6264 - val_loss: 2.4291 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6716 - loss: 0.6040 - val_accuracy: 0.6281 - val_loss: 2.2117 - learning_rate: 0.0010
Epoch 95/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6571 - loss:

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.6827 - loss: 0.5944 - val_accuracy: 0.4812 - val_loss: 1.3430 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7005 - loss: 0.5802 - val_accuracy: 0.4095 - val_loss: 2.4940 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6867 - loss: 0.5787 - val_accuracy: 0.6493 - val_loss: 1.1038 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.6713 - loss: 0.5890 - val_accuracy: 0.5073 - val_loss: 1.1425 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 7ms/step - accuracy: 0.6791 - loss: 0.6078 - val_accuracy: 0.6607 - val_loss: 0.8981 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7016 - loss: 0.6045 - val_accuracy: 0.6542 - val_loss: 0.9830 - learning_rate: 0.0010
Epoch 138/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6881 - loss: 0.5945

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6929 - loss: 0.5856 - val_accuracy: 0.6591 - val_loss: 0.8773 - learning_rate: 5.0000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6524 - loss: 0.6090 - val_accuracy: 0.6656 - val_loss: 0.8203 - learning_rate: 5.0000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7013 - loss: 0.5825 - val_accuracy: 0.6819 - val_loss: 0.6959 - learning_rate: 5.0000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - accuracy: 0.6624 - loss: 0.6013 - val_accuracy: 0.6721 - val_loss: 0.7452 - learning_rate: 5.0000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7188 - loss: 0.5812 - val_accuracy: 0.5155 - val_loss: 1.1726 - learning_rate: 5.0000e-04
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6790 - loss: 0.5981 - val_accuracy: 0.6868 - val_loss: 0.6608 - learning_rate: 5.0000e-04
Epoch 181/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accurac

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.6867 - loss: 0.5596 - val_accuracy: 0.4878 - val_loss: 1.9919 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6984 - loss: 0.5731 - val_accuracy: 0.5318 - val_loss: 1.4145 - learning_rate: 1.0000e-04
Epoch 1819/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7045 - loss: 0.5952 - val_accuracy: 0.5302 - val_loss: 1.4680 - learning_rate: 1.0000e-04
Epoch 1820/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.6895 - loss: 0.5854 - val_accuracy: 0.5269 - val_loss: 1.4897 - learning_rate: 1.0000e-04
Epoch 1821/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.6983 - loss: 0.5716 - val_accuracy: 0.7031 - val_loss: 0.7990 - learning_rate: 1.0000e-04
Epoch 1822/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7212 - loss: 0.5767 - val_accuracy: 0.6330 - val_loss: 0.9490 - learning_rate: 1.0000e-04
Epoch 1823/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 6ms/step - accuracy: 0.7196 - loss: 0.5625 - val_accuracy: 0.6705 - val_loss: 0.8591 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7463 - loss: 0.5495 - val_accuracy: 0.6754 - val_loss: 0.8643 - learning_rate: 1.0000e-04
Epoch 1861/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7181 - loss: 0.5592 - val_accuracy: 0.4617 - val_loss: 2.4416 - learning_rate: 1.0000e-04
Epoch 1862/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - accuracy: 0.7414 - loss: 0.5387 - val_accuracy: 0.5155 - val_loss: 1.4767 - learning_rate: 1.0000e-04
Epoch 1863/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6947 - loss: 0.5764 - val_accuracy: 0.7015 - val_loss: 0.7952 - learning_rate: 1.0000e-04
Epoch 1864/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7325 - loss: 0.5568 - val_accuracy: 0.4959 - val_loss: 1.8665 - learning_rate: 1.0000e-04
Epoch 1865/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7550 - loss: 0.5402 - val_accuracy: 0.4992 - val_loss: 1.8331 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7183 - loss: 0.5296 - val_accuracy: 0.6705 - val_loss: 0.8795 - learning_rate: 1.0000e-04
Epoch 1903/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6989 - loss: 0.5566 - val_accuracy: 0.5889 - val_loss: 1.1012 - learning_rate: 1.0000e-04
Epoch 1904/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7586 - loss: 0.5346 - val_accuracy: 0.4633 - val_loss: 2.5092 - learning_rate: 1.0000e-04
Epoch 1905/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7017 - loss: 0.5718 - val_accuracy: 0.5318 - val_loss: 1.4139 - learning_rate: 1.0000e-04
Epoch 1906/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7319 - loss: 0.5594 - val_accuracy: 0.5693 - val_loss: 1.1729 - learning_rate: 1.0000e-04
Epoch 1907/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step -

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.6854 - loss: 0.5890 - val_accuracy: 0.7113 - val_loss: 0.7577 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7134 - loss: 0.5604 - val_accuracy: 0.4258 - val_loss: 3.4711 - learning_rate: 1.0000e-04
Epoch 1945/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6924 - loss: 0.5678 - val_accuracy: 0.5481 - val_loss: 1.2872 - learning_rate: 1.0000e-04
Epoch 1946/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7290 - loss: 0.5521 - val_accuracy: 0.5514 - val_loss: 1.2451 - learning_rate: 1.0000e-04
Epoch 1947/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7062 - loss: 0.5629 - val_accuracy: 0.5057 - val_loss: 1.7051 - learning_rate: 1.0000e-04
Epoch 1948/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.7189 - loss: 0.5892 - val_accuracy: 0.6852 - val_loss: 0.8028 - learning_rate: 1.0000e-04
Epoch 1949/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step -

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - accuracy: 0.7206 - loss: 0.5525 - val_accuracy: 0.6444 - val_loss: 0.9364 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7086 - loss: 0.5847 - val_accuracy: 0.5873 - val_loss: 1.1289 - learning_rate: 1.0000e-04
Epoch 1987/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7265 - loss: 0.5456 - val_accuracy: 0.5334 - val_loss: 1.4436 - learning_rate: 1.0000e-04
Epoch 1988/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7419 - loss: 0.5152 - val_accuracy: 0.4747 - val_loss: 2.2899 - learning_rate: 1.0000e-04
Epoch 1989/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7254 - loss: 0.5523 - val_accuracy: 0.4731 - val_loss: 2.3947 - learning_rate: 1.0000e-04
Epoch 1990/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - accuracy: 0.6805 - loss: 0.5668 - val_accuracy: 0.7064 - val_loss: 0.7638 - learning_rate: 1.0000e-04
Epoch 1991/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step -

In [7]:
#FCN-VI

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('relu')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('relu')(conv2)
    
#    drop_out = Dropout(0.2)(conv2)
#    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
#    conv3 = keras.layers.Activation('relu')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv2)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist6 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log6 = pd.DataFrame(hist6.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_model6
fcn_model6 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 6s 40ms/step - accuracy: 0.5199 - loss: 1.0184 - val_accuracy: 0.6215 - val_loss: 0.6720 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.5789 - loss: 0.6801 - val_accuracy: 0.4209 - val_loss: 0.6945 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6289 - loss: 0.6504 - val_accuracy: 0.3801 - val_loss: 1.0210 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.6255 - loss: 0.6620 - val_accuracy: 0.4176 - val_loss: 0.7048 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6349 - loss: 0.6381 - val_accuracy: 0.6199 - val_loss: 1.1289 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6788 - loss: 0.6104 - val_accuracy: 0.6542 - val_loss: 0.6173 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6869 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7124 - loss: 0.5593 - val_accuracy: 0.6362 - val_loss: 1.9959 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7149 - loss: 0.5688 - val_accuracy: 0.6199 - val_loss: 4.8330 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7227 - loss: 0.5630 - val_accuracy: 0.6542 - val_loss: 1.4054 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6926 - loss: 0.5921 - val_accuracy: 0.3801 - val_loss: 8.9515 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6986 - loss: 0.5941 - val_accuracy: 0.6199 - val_loss: 4.3030 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7033 - loss: 0.5766 - val_accuracy: 0.6232 - val_loss: 2.8102 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7122 - loss: 0.5894 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6901 - loss: 0.6068 - val_accuracy: 0.5220 - val_loss: 1.3436 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7608 - loss: 0.5419 - val_accuracy: 0.6264 - val_loss: 2.6962 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7212 - loss: 0.5419 - val_accuracy: 0.3817 - val_loss: 6.1349 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6946 - loss: 0.5817 - val_accuracy: 0.6721 - val_loss: 1.0700 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7188 - loss: 0.5726 - val_accuracy: 0.5432 - val_loss: 1.2483 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7164 - loss: 0.5705 - val_accuracy: 0.3883 - val_loss: 5.9374 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6860 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 18ms/step - accuracy: 0.7209 - loss: 0.5585 - val_accuracy: 0.6819 - val_loss: 0.9609 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7176 - loss: 0.5434 - val_accuracy: 0.6835 - val_loss: 1.0076 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7095 - loss: 0.5550 - val_accuracy: 0.6966 - val_loss: 0.7440 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6854 - loss: 0.5515 - val_accuracy: 0.6786 - val_loss: 1.0626 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7013 - loss: 0.5514 - val_accuracy: 0.6542 - val_loss: 0.8810 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7169 - loss: 0.5581 - val_accuracy: 0.6672 - val_loss: 1.1559 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7149 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7598 - loss: 0.5194 - val_accuracy: 0.4519 - val_loss: 2.1661 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7531 - loss: 0.4927 - val_accuracy: 0.6933 - val_loss: 0.7908 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7353 - loss: 0.5187 - val_accuracy: 0.6623 - val_loss: 1.4908 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7287 - loss: 0.5469 - val_accuracy: 0.6395 - val_loss: 2.8904 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7178 - loss: 0.5434 - val_accuracy: 0.6313 - val_loss: 3.3258 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7142 - loss: 0.5341 - val_accuracy: 0.6199 - val_loss: 9.4515 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7054 - loss: 0.5

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.9979 - loss: 0.0397 - val_accuracy: 0.4078 - val_loss: 62.2046 - learning_rate: 1.0000e-04
Epoch 1795/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.9963 - loss: 0.0361 - val_accuracy: 0.4078 - val_loss: 60.7557 - learning_rate: 1.0000e-04
Epoch 1796/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.9981 - loss: 0.0426 - val_accuracy: 0.4078 - val_loss: 60.3042 - learning_rate: 1.0000e-04
Epoch 1797/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.9938 - loss: 0.0553 - val_accuracy: 0.4078 - val_loss: 62.0273 - learning_rate: 1.0000e-04
Epoch 1798/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.9999 - loss: 0.0367 - val_accuracy: 0.4046 - val_loss: 61.5575 - learning_rate: 1.0000e-04
Epoch 1799/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9924 - loss: 0.0444 - val_accuracy: 0.4062 - val_loss: 60.5478 - learning_rate: 1.0000e-04
Epoch 1800/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.9872 - loss: 0.0541 - val_accuracy: 0.4127 - val_loss: 60.3148 - learning_rate: 1.0000e-04
Epoch 1837/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9874 - loss: 0.0449 - val_accuracy: 0.4160 - val_loss: 51.6840 - learning_rate: 1.0000e-04
Epoch 1838/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.9934 - loss: 0.0360 - val_accuracy: 0.4078 - val_loss: 58.4815 - learning_rate: 1.0000e-04
Epoch 1839/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.9959 - loss: 0.0390 - val_accuracy: 0.4078 - val_loss: 58.9613 - learning_rate: 1.0000e-04
Epoch 1840/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9998 - loss: 0.0354 - val_accuracy: 0.4062 - val_loss: 58.3544 - learning_rate: 1.0000e-04
Epoch 1841/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9954 - loss: 0.0359 - val_accuracy: 0.4192 - val_loss: 43.3814 - learning_rate: 1.0000e-04
Epoch 1842/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.9750 - loss: 0.0583 - val_accuracy: 0.4160 - val_loss: 45.0505 - learning_rate: 1.0000e-04
Epoch 1879/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.9955 - loss: 0.0431 - val_accuracy: 0.4127 - val_loss: 48.7875 - learning_rate: 1.0000e-04
Epoch 1880/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9988 - loss: 0.0407 - val_accuracy: 0.4127 - val_loss: 49.6650 - learning_rate: 1.0000e-04
Epoch 1881/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9920 - loss: 0.0453 - val_accuracy: 0.4176 - val_loss: 43.7758 - learning_rate: 1.0000e-04
Epoch 1882/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9943 - loss: 0.0401 - val_accuracy: 0.4144 - val_loss: 47.5336 - learning_rate: 1.0000e-04
Epoch 1883/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9938 - loss: 0.0353 - val_accuracy: 0.4192 - val_loss: 42.2700 - learning_rate: 1.0000e-04
Epoch 1884/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.9943 - loss: 0.0402 - val_accuracy: 0.4127 - val_loss: 45.4751 - learning_rate: 1.0000e-04
Epoch 1921/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.9933 - loss: 0.0419 - val_accuracy: 0.4225 - val_loss: 40.0495 - learning_rate: 1.0000e-04
Epoch 1922/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.9992 - loss: 0.0305 - val_accuracy: 0.4144 - val_loss: 43.1763 - learning_rate: 1.0000e-04
Epoch 1923/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.9972 - loss: 0.0352 - val_accuracy: 0.4192 - val_loss: 38.3962 - learning_rate: 1.0000e-04
Epoch 1924/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.9973 - loss: 0.0331 - val_accuracy: 0.4225 - val_loss: 39.7404 - learning_rate: 1.0000e-04
Epoch 1925/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.9909 - loss: 0.0424 - val_accuracy: 0.4192 - val_loss: 37.9336 - learning_rate: 1.0000e-04
Epoch 1926/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.9946 - loss: 0.0332 - val_accuracy: 0.4111 - val_loss: 45.7035 - learning_rate: 1.0000e-04
Epoch 1963/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.9953 - loss: 0.0463 - val_accuracy: 0.4127 - val_loss: 45.0491 - learning_rate: 1.0000e-04
Epoch 1964/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.9926 - loss: 0.0333 - val_accuracy: 0.4046 - val_loss: 51.2240 - learning_rate: 1.0000e-04
Epoch 1965/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.9978 - loss: 0.0307 - val_accuracy: 0.4046 - val_loss: 50.0013 - learning_rate: 1.0000e-04
Epoch 1966/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.9968 - loss: 0.0358 - val_accuracy: 0.4144 - val_loss: 44.8232 - learning_rate: 1.0000e-04
Epoch 1967/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.9957 - loss: 0.0376 - val_accuracy: 0.4095 - val_loss: 47.3270 - learning_rate: 1.0000e-04
Epoch 1968/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms

In [8]:
#FCN-VII

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('relu')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('relu')(conv2)
    

    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.Activation('relu')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv3)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist7 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log7 = pd.DataFrame(hist7.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_model7
fcn_model7 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 10s 56ms/step - accuracy: 0.5471 - loss: 0.8398 - val_accuracy: 0.5400 - val_loss: 0.6877 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.5262 - loss: 0.7004 - val_accuracy: 0.3834 - val_loss: 0.7373 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.5448 - loss: 0.6951 - val_accuracy: 0.6199 - val_loss: 0.6628 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6601 - loss: 0.6411 - val_accuracy: 0.5302 - val_loss: 0.6898 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6509 - loss: 0.6351 - val_accuracy: 0.6199 - val_loss: 0.6716 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.6125 - loss: 0.6610 - val_accuracy: 0.6607 - val_loss: 0.6671 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6129 - loss: 0

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7138 - loss: 0.5718 - val_accuracy: 0.3801 - val_loss: 6.2822 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.6715 - loss: 0.6114 - val_accuracy: 0.3997 - val_loss: 3.1473 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6809 - loss: 0.5786 - val_accuracy: 0.6281 - val_loss: 1.8146 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7285 - loss: 0.5439 - val_accuracy: 0.6346 - val_loss: 0.6987 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.7237 - loss: 0.5723 - val_accuracy: 0.4209 - val_loss: 2.0023 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6883 - loss: 0.5665 - val_accuracy: 0.6949 - val_loss: 0.6822 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7084 - loss: 0.5674 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 3s 34ms/step - accuracy: 0.7279 - loss: 0.5562 - val_accuracy: 0.6623 - val_loss: 1.1867 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 3s 34ms/step - accuracy: 0.7147 - loss: 0.5512 - val_accuracy: 0.4649 - val_loss: 1.1426 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.7247 - loss: 0.5492 - val_accuracy: 0.6754 - val_loss: 0.9475 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7173 - loss: 0.5388 - val_accuracy: 0.6656 - val_loss: 1.1650 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7520 - loss: 0.5126 - val_accuracy: 0.5661 - val_loss: 0.9298 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7330 - loss: 0.5315 - val_accuracy: 0.6264 - val_loss: 2.4251 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.6964 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7527 - loss: 0.5142 - val_accuracy: 0.6949 - val_loss: 0.6905 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7610 - loss: 0.5008 - val_accuracy: 0.4682 - val_loss: 1.6104 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 36ms/step - accuracy: 0.7355 - loss: 0.5297 - val_accuracy: 0.4894 - val_loss: 1.5418 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7530 - loss: 0.5002 - val_accuracy: 0.6835 - val_loss: 0.6679 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.7555 - loss: 0.5100 - val_accuracy: 0.6672 - val_loss: 0.7733 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7503 - loss: 0.5080 - val_accuracy: 0.4617 - val_loss: 1.7750 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7758 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7775 - loss: 0.4535 - val_accuracy: 0.6966 - val_loss: 0.6787 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7637 - loss: 0.4588 - val_accuracy: 0.4144 - val_loss: 3.2866 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7837 - loss: 0.4626 - val_accuracy: 0.6688 - val_loss: 0.7708 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7809 - loss: 0.4697 - val_accuracy: 0.4127 - val_loss: 3.0730 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7868 - loss: 0.4686 - val_accuracy: 0.4225 - val_loss: 2.8914 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7766 - loss: 0.4719 - val_accuracy: 0.7047 - val_loss: 0.6574 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7526 - loss: 0.4

...

Epoch 1828/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 1.0000 - loss: 5.6504e-04 - val_accuracy: 0.4356 - val_loss: 23.3067 - learning_rate: 1.0000e-04
Epoch 1829/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 9.0145e-04 - val_accuracy: 0.4388 - val_loss: 22.9432 - learning_rate: 1.0000e-04
Epoch 1830/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.4551 - val_loss: 20.5689 - learning_rate: 1.0000e-04
Epoch 1831/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 1.0000 - loss: 0.0014 - val_accuracy: 0.4551 - val_loss: 21.4108 - learning_rate: 1.0000e-04
Epoch 1832/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 1.0000 - loss: 0.0011 - val_accuracy: 0.4535 - val_loss: 21.0933 - learning_rate: 1.0000e-04
Epoch 1833/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 39ms/step - accuracy: 1.0000 - loss: 0.0016 - val_accuracy: 0.4470 - val_loss: 21.6587 - learning_rate: 1.0000e-04
Epoch 1834/2000
37/37 ━━━━

Epoch 1870/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 3s 38ms/step - accuracy: 0.9980 - loss: 0.0080 - val_accuracy: 0.4894 - val_loss: 13.0159 - learning_rate: 1.0000e-04
Epoch 1871/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 0.0029 - val_accuracy: 0.4976 - val_loss: 11.7362 - learning_rate: 1.0000e-04
Epoch 1872/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 3s 39ms/step - accuracy: 1.0000 - loss: 0.0026 - val_accuracy: 0.4910 - val_loss: 13.6006 - learning_rate: 1.0000e-04
Epoch 1873/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 39ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.4812 - val_loss: 15.1591 - learning_rate: 1.0000e-04
Epoch 1874/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 1.0000 - loss: 0.0017 - val_accuracy: 0.4943 - val_loss: 12.1611 - learning_rate: 1.0000e-04
Epoch 1875/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 0.0015 - val_accuracy: 0.4878 - val_loss: 13.3742 - learning_rate: 1.0000e-04
Epoch 1876/2000
37/37 ━━━━━━━━━━━━

Epoch 1912/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.4763 - val_loss: 17.5933 - learning_rate: 1.0000e-04
Epoch 1913/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 0.0022 - val_accuracy: 0.4763 - val_loss: 17.7098 - learning_rate: 1.0000e-04
Epoch 1914/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 0.0021 - val_accuracy: 0.4600 - val_loss: 20.7113 - learning_rate: 1.0000e-04
Epoch 1915/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.9955 - loss: 0.0092 - val_accuracy: 0.4405 - val_loss: 26.1731 - learning_rate: 1.0000e-04
Epoch 1916/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.9980 - loss: 0.0041 - val_accuracy: 0.4600 - val_loss: 20.8183 - learning_rate: 1.0000e-04
Epoch 1917/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 0.0090 - val_accuracy: 0.4437 - val_loss: 22.6264 - learning_rate: 1.0000e-04
Epoch 1918/2000
37/37 ━━━━━━━━━━━━

Epoch 1954/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 0.0014 - val_accuracy: 0.4600 - val_loss: 18.6371 - learning_rate: 1.0000e-04
Epoch 1955/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 0.0012 - val_accuracy: 0.4698 - val_loss: 17.8174 - learning_rate: 1.0000e-04
Epoch 1956/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.9998 - loss: 0.0037 - val_accuracy: 0.4486 - val_loss: 20.2841 - learning_rate: 1.0000e-04
Epoch 1957/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.9988 - loss: 0.0024 - val_accuracy: 0.4633 - val_loss: 18.8044 - learning_rate: 1.0000e-04
Epoch 1958/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 0.0015 - val_accuracy: 0.4600 - val_loss: 19.2646 - learning_rate: 1.0000e-04
Epoch 1959/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 0.0021 - val_accuracy: 0.4584 - val_loss: 20.1410 - learning_rate: 1.0000e-04
Epoch 1960/2000
37/37 ━━━━━━━━━━━━

Epoch 1996/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 0.0021 - val_accuracy: 0.4878 - val_loss: 12.5538 - learning_rate: 1.0000e-04
Epoch 1997/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.9973 - loss: 0.0039 - val_accuracy: 0.4796 - val_loss: 16.7525 - learning_rate: 1.0000e-04
Epoch 1998/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 0.0034 - val_accuracy: 0.4976 - val_loss: 13.1660 - learning_rate: 1.0000e-04
Epoch 1999/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 0.0017 - val_accuracy: 0.4731 - val_loss: 16.7092 - learning_rate: 1.0000e-04
Epoch 2000/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 3s 35ms/step - accuracy: 1.0000 - loss: 0.0039 - val_accuracy: 0.4894 - val_loss: 13.1892 - learning_rate: 1.0000e-04


In [9]:
#FCN-VIII

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('relu')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('relu')(conv2)
    

    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.Activation('relu')(conv3)


    conv4 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv3)
    conv4 = keras.layers.BatchNormalization()(conv4)
    conv4 = keras.layers.Activation('relu')(conv4)
    
    full = keras.layers.GlobalAveragePooling2D()(conv4)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist8 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log8 = pd.DataFrame(hist8.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_model8
fcn_model8 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 13s 66ms/step - accuracy: 0.5167 - loss: 0.8612 - val_accuracy: 0.4519 - val_loss: 0.6937 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 41ms/step - accuracy: 0.6022 - loss: 0.6921 - val_accuracy: 0.6199 - val_loss: 0.6955 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 40ms/step - accuracy: 0.5670 - loss: 0.6851 - val_accuracy: 0.6199 - val_loss: 0.6711 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.5835 - loss: 0.6815 - val_accuracy: 0.3899 - val_loss: 0.7131 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 39ms/step - accuracy: 0.6198 - loss: 0.6559 - val_accuracy: 0.4486 - val_loss: 0.7156 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.6328 - loss: 0.6433 - val_accuracy: 0.6199 - val_loss: 1.1745 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 46ms/step - accuracy: 0.6172 - loss: 0

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 39ms/step - accuracy: 0.7149 - loss: 0.5714 - val_accuracy: 0.4845 - val_loss: 1.0473 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.6737 - loss: 0.5869 - val_accuracy: 0.4046 - val_loss: 2.0017 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 40ms/step - accuracy: 0.7113 - loss: 0.5681 - val_accuracy: 0.6199 - val_loss: 4.3853 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 40ms/step - accuracy: 0.6950 - loss: 0.5776 - val_accuracy: 0.4176 - val_loss: 2.2645 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 42ms/step - accuracy: 0.7002 - loss: 0.5651 - val_accuracy: 0.6330 - val_loss: 2.0956 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.6834 - loss: 0.5901 - val_accuracy: 0.6542 - val_loss: 1.1283 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 45ms/step - accuracy: 0.6760 - loss: 0.5791 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.7427 - loss: 0.5281 - val_accuracy: 0.4290 - val_loss: 1.4402 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 38ms/step - accuracy: 0.7060 - loss: 0.5309 - val_accuracy: 0.4894 - val_loss: 1.2123 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.7185 - loss: 0.5361 - val_accuracy: 0.6852 - val_loss: 0.7386 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.7414 - loss: 0.5334 - val_accuracy: 0.3883 - val_loss: 4.1612 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.7325 - loss: 0.5385 - val_accuracy: 0.6754 - val_loss: 0.6702 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 39ms/step - accuracy: 0.7315 - loss: 0.5298 - val_accuracy: 0.6688 - val_loss: 0.9158 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 0.7315 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.7788 - loss: 0.4688 - val_accuracy: 0.6819 - val_loss: 0.8371 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 3s 39ms/step - accuracy: 0.7762 - loss: 0.4636 - val_accuracy: 0.7031 - val_loss: 0.6460 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 43ms/step - accuracy: 0.7623 - loss: 0.4744 - val_accuracy: 0.5922 - val_loss: 1.0651 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7772 - loss: 0.4466 - val_accuracy: 0.7031 - val_loss: 0.6830 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 39ms/step - accuracy: 0.7903 - loss: 0.4442 - val_accuracy: 0.6623 - val_loss: 1.0628 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.7975 - loss: 0.4546 - val_accuracy: 0.6917 - val_loss: 0.9871 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.8091 - loss: 0.4

37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 40ms/step - accuracy: 0.8365 - loss: 0.3653 - val_accuracy: 0.6639 - val_loss: 1.2571 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.8163 - loss: 0.3919 - val_accuracy: 0.6623 - val_loss: 1.5367 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 41ms/step - accuracy: 0.8626 - loss: 0.3307 - val_accuracy: 0.3997 - val_loss: 2.5208 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 41ms/step - accuracy: 0.8194 - loss: 0.3736 - val_accuracy: 0.5546 - val_loss: 1.1495 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 39ms/step - accuracy: 0.8127 - loss: 0.3913 - val_accuracy: 0.5938 - val_loss: 0.8026 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 41ms/step - accuracy: 0.8313 - loss: 0.4044 - val_accuracy: 0.5237 - val_loss: 1.1700 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 35ms/step - accuracy: 0.8371 - loss: 0.3

...

Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 1.0000 - loss: 6.9485e-04 - val_accuracy: 0.4845 - val_loss: 10.8700 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 1.0000 - loss: 8.4148e-04 - val_accuracy: 0.4796 - val_loss: 11.2799 - learning_rate: 1.0000e-04
Epoch 1819/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 4.6136e-04 - val_accuracy: 0.4796 - val_loss: 11.2011 - learning_rate: 1.0000e-04
Epoch 1820/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.9955 - loss: 0.0044 - val_accuracy: 0.4666 - val_loss: 11.6945 - learning_rate: 1.0000e-04
Epoch 1821/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 9.8586e-04 - val_accuracy: 0.4910 - val_loss: 10.1398 - learning_rate: 1.0000e-04
Epoch 1822/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 1.0000 - loss: 6.1050e-04 - val_accuracy: 0.5106 - val_loss: 9.5053 - learning_rate: 1.0000e-04
Epoch 1823/2000

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 1.0000 - loss: 2.7743e-04 - val_accuracy: 0.4878 - val_loss: 10.2455 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 2.6241e-04 - val_accuracy: 0.4829 - val_loss: 10.3364 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 2.8182e-04 - val_accuracy: 0.4943 - val_loss: 9.9538 - learning_rate: 1.0000e-04
Epoch 1861/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 1.8987e-04 - val_accuracy: 0.4878 - val_loss: 10.1345 - learning_rate: 1.0000e-04
Epoch 1862/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 1.0000 - loss: 2.4578e-04 - val_accuracy: 0.4943 - val_loss: 9.9089 - learning_rate: 1.0000e-04
Epoch 1863/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 1.6450e-04 - val_accuracy: 0.4992 - val_loss: 9.7696 - learning_rate: 1.0000e-04
Epoch 1864/2000
37/37 ━━━━━━━

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 0.0014 - val_accuracy: 0.4763 - val_loss: 10.8384 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 1.0000 - loss: 0.0015 - val_accuracy: 0.4927 - val_loss: 9.7305 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 6.8693e-04 - val_accuracy: 0.4959 - val_loss: 9.6331 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 3.7200e-04 - val_accuracy: 0.4943 - val_loss: 9.9835 - learning_rate: 1.0000e-04
Epoch 1903/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 1.0000 - loss: 4.2720e-04 - val_accuracy: 0.4894 - val_loss: 10.1037 - learning_rate: 1.0000e-04
Epoch 1904/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 42ms/step - accuracy: 1.0000 - loss: 1.9520e-04 - val_accuracy: 0.4927 - val_loss: 9.9590 - learning_rate: 1.0000e-04
Epoch 1905/2000
37/37 ━━━━━━━━━━━━━━━━

Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.9955 - loss: 0.0047 - val_accuracy: 0.5856 - val_loss: 5.1909 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 3.5699e-04 - val_accuracy: 0.5856 - val_loss: 5.2267 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 1.0000 - loss: 6.8179e-04 - val_accuracy: 0.5889 - val_loss: 5.1901 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 6.8668e-04 - val_accuracy: 0.6003 - val_loss: 5.2247 - learning_rate: 1.0000e-04
Epoch 1945/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 39ms/step - accuracy: 1.0000 - loss: 4.6206e-04 - val_accuracy: 0.5840 - val_loss: 5.5800 - learning_rate: 1.0000e-04
Epoch 1946/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 1.0000 - loss: 6.7471e-04 - val_accuracy: 0.5905 - val_loss: 5.5001 - learning_rate: 1.0000e-04
Epoch 1947/2000
37/3

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 37ms/step - accuracy: 1.0000 - loss: 2.2109e-04 - val_accuracy: 0.5563 - val_loss: 5.5520 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 1.0000 - loss: 2.5991e-04 - val_accuracy: 0.5661 - val_loss: 5.4007 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 1.0000 - loss: 3.9869e-04 - val_accuracy: 0.5514 - val_loss: 5.5375 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 3.9429e-04 - val_accuracy: 0.5628 - val_loss: 5.2920 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 1.1998e-04 - val_accuracy: 0.5693 - val_loss: 5.1945 - learning_rate: 1.0000e-04
Epoch 1987/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 1.0000 - loss: 9.6352e-05 - val_accuracy: 0.5742 - val_loss: 5.1493 - learning_rate: 1.0000e-04
Epoch 1988/2000
37/37 ━━━━━━━━━━

In [10]:
#FCN-IX

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
#    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('linear')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
#    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
#    conv2 = keras.layers.Activation(''linear')(conv2)
    
#    drop_out = Dropout(0.2)(conv2)
#    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
#    conv3 = keras.layers.Activation('linear')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv1)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
    hist9 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
    log9 = pd.DataFrame(hist9.history)
 #   print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_model9
fcn_model9 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 3s 25ms/step - accuracy: 0.5359 - loss: 0.6960 - val_accuracy: 0.6199 - val_loss: 1.2756 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.5653 - loss: 0.6747 - val_accuracy: 0.3850 - val_loss: 0.9166 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.5607 - loss: 0.6882 - val_accuracy: 0.6199 - val_loss: 0.7295 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.5985 - loss: 0.6746 - val_accuracy: 0.6199 - val_loss: 0.8970 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.5730 - loss: 0.6791 - val_accuracy: 0.6199 - val_loss: 0.7294 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.6023 - loss: 0.6697 - val_accuracy: 0.6199 - val_loss: 1.1951 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.5898 - loss: 0.

Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6641 - loss: 0.6197 - val_accuracy: 0.6476 - val_loss: 1.1036 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7097 - loss: 0.5767 - val_accuracy: 0.6982 - val_loss: 0.6896 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7050 - loss: 0.5811 - val_accuracy: 0.6542 - val_loss: 0.7468 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7038 - loss: 0.5798 - val_accuracy: 0.6868 - val_loss: 0.6701 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6899 - loss: 0.5853 - val_accuracy: 0.4894 - val_loss: 1.3856 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6878 - loss: 0.6015 - val_accuracy: 0.6591 - val_loss: 0.8076 - learning_rate: 0.0010
Epoch 51/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6784 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7093 - loss: 0.5749 - val_accuracy: 0.5791 - val_loss: 0.9464 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - accuracy: 0.7238 - loss: 0.5836 - val_accuracy: 0.6803 - val_loss: 0.7118 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.7090 - loss: 0.5872 - val_accuracy: 0.6395 - val_loss: 1.8088 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.6850 - loss: 0.5790 - val_accuracy: 0.6395 - val_loss: 1.6584 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6772 - loss: 0.6323 - val_accuracy: 0.6656 - val_loss: 0.8894 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.7094 - loss: 0.5879 - val_accuracy: 0.4046 - val_loss: 3.0826 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.6665 - loss: 0.6132 - va

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.6665 - loss: 0.6068 - val_accuracy: 0.7113 - val_loss: 0.6782 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7208 - loss: 0.5667 - val_accuracy: 0.5155 - val_loss: 1.2582 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.6661 - loss: 0.6088 - val_accuracy: 0.6884 - val_loss: 0.6921 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7204 - loss: 0.5741 - val_accuracy: 0.5432 - val_loss: 1.0707 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7370 - loss: 0.5533 - val_accuracy: 0.7096 - val_loss: 0.6802 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7304 - loss: 0.5435 - val_accuracy: 0.6362 - val_loss: 1.9588 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6736 - loss: 0.6

Epoch 174/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.6993 - loss: 0.5644 - val_accuracy: 0.6966 - val_loss: 0.7163 - learning_rate: 5.0000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7038 - loss: 0.5646 - val_accuracy: 0.6607 - val_loss: 0.8286 - learning_rate: 5.0000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - accuracy: 0.7169 - loss: 0.5878 - val_accuracy: 0.6852 - val_loss: 0.7577 - learning_rate: 5.0000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7064 - loss: 0.5474 - val_accuracy: 0.7031 - val_loss: 0.6917 - learning_rate: 5.0000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7137 - loss: 0.5807 - val_accuracy: 0.6656 - val_loss: 0.9105 - learning_rate: 5.0000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6938 - loss: 0.6002 - val_accuracy: 0.7031 - val_loss: 0.6903 - learning_rate: 5.0000e-04
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7039 - loss: 0.5965 - val_accuracy: 0.6868 - val_loss: 0.7748 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.6989 - loss: 0.6089 - val_accuracy: 0.6852 - val_loss: 0.8198 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7151 - loss: 0.5551 - val_accuracy: 0.6900 - val_loss: 0.7406 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - accuracy: 0.7259 - loss: 0.5564 - val_accuracy: 0.6868 - val_loss: 0.7388 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6984 - loss: 0.5729 - val_accuracy: 0.6917 - val_loss: 0.7281 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7312 - loss: 0.5540 - val_accuracy: 0.6852 - val_loss: 0.7610 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step -

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7110 - loss: 0.5657 - val_accuracy: 0.6884 - val_loss: 0.8063 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.7201 - loss: 0.5720 - val_accuracy: 0.6770 - val_loss: 0.8637 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6909 - loss: 0.5842 - val_accuracy: 0.6868 - val_loss: 0.7767 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7358 - loss: 0.5563 - val_accuracy: 0.6852 - val_loss: 0.7662 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7259 - loss: 0.5579 - val_accuracy: 0.6917 - val_loss: 0.7280 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6798 - loss: 0.5919 - val_accuracy: 0.6884 - val_loss: 0.7734 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - ac

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7134 - loss: 0.5519 - val_accuracy: 0.6868 - val_loss: 0.7481 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7313 - loss: 0.5538 - val_accuracy: 0.6917 - val_loss: 0.7289 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6957 - loss: 0.5684 - val_accuracy: 0.6803 - val_loss: 0.8590 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7143 - loss: 0.5690 - val_accuracy: 0.6917 - val_loss: 0.7162 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.7023 - loss: 0.5818 - val_accuracy: 0.6917 - val_loss: 0.7252 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6925 - loss: 0.5732 - val_accuracy: 0.6917 - val_loss: 0.7242 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - a

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7006 - loss: 0.5653 - val_accuracy: 0.6803 - val_loss: 0.7900 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6866 - loss: 0.5990 - val_accuracy: 0.6852 - val_loss: 0.7672 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7122 - loss: 0.5657 - val_accuracy: 0.6966 - val_loss: 0.7199 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.6996 - loss: 0.5674 - val_accuracy: 0.6852 - val_loss: 0.8186 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7004 - loss: 0.5819 - val_accuracy: 0.6884 - val_loss: 0.7709 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 9ms/step - accuracy: 0.7083 - loss: 0.5798 - val_accuracy: 0.6900 - val_loss: 0.7229 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - a

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - accuracy: 0.7037 - loss: 0.5898 - val_accuracy: 0.6900 - val_loss: 0.7310 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.6922 - loss: 0.5955 - val_accuracy: 0.6852 - val_loss: 0.7629 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7346 - loss: 0.5609 - val_accuracy: 0.6852 - val_loss: 0.7930 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7318 - loss: 0.5411 - val_accuracy: 0.6852 - val_loss: 0.7664 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7159 - loss: 0.5768 - val_accuracy: 0.6917 - val_loss: 0.7240 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6589 - loss: 0.6135 - val_accuracy: 0.6819 - val_loss: 0.7566 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step 

In [11]:
#FCN-X

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
#    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('linear')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('linear')(conv2)
    
#    drop_out = Dropout(0.2)(conv2)
#    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
#    conv3 = keras.layers.Activation('linear')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv2)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist10 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log10 = pd.DataFrame(hist10.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_model10
fcn_model10 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 5s 40ms/step - accuracy: 0.5494 - loss: 0.6888 - val_accuracy: 0.3948 - val_loss: 0.7928 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.5870 - loss: 0.6773 - val_accuracy: 0.6199 - val_loss: 1.2399 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.5811 - loss: 0.6716 - val_accuracy: 0.6199 - val_loss: 1.2280 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.5775 - loss: 0.6771 - val_accuracy: 0.6199 - val_loss: 1.9702 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.5707 - loss: 0.6660 - val_accuracy: 0.6199 - val_loss: 1.7663 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6265 - loss: 0.6341 - val_accuracy: 0.6639 - val_loss: 0.6132 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.5865 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7133 - loss: 0.5888 - val_accuracy: 0.4405 - val_loss: 2.0702 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7159 - loss: 0.5892 - val_accuracy: 0.6264 - val_loss: 2.9586 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7225 - loss: 0.5862 - val_accuracy: 0.6574 - val_loss: 1.0802 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7205 - loss: 0.5873 - val_accuracy: 0.6493 - val_loss: 1.5462 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6850 - loss: 0.5767 - val_accuracy: 0.6264 - val_loss: 3.3726 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6725 - loss: 0.6069 - val_accuracy: 0.6150 - val_loss: 0.8270 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7310 - loss: 0.5717 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7361 - loss: 0.5516 - val_accuracy: 0.5106 - val_loss: 1.3371 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6971 - loss: 0.5942 - val_accuracy: 0.7015 - val_loss: 0.7537 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6951 - loss: 0.5845 - val_accuracy: 0.7080 - val_loss: 0.6988 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7444 - loss: 0.5521 - val_accuracy: 0.4584 - val_loss: 1.7925 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7114 - loss: 0.5670 - val_accuracy: 0.6721 - val_loss: 0.7908 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7031 - loss: 0.5746 - val_accuracy: 0.6476 - val_loss: 1.7423 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7046 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7081 - loss: 0.5956 - val_accuracy: 0.7129 - val_loss: 0.7008 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7273 - loss: 0.5706 - val_accuracy: 0.6819 - val_loss: 0.8791 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7182 - loss: 0.5696 - val_accuracy: 0.6199 - val_loss: 0.9021 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7093 - loss: 0.5614 - val_accuracy: 0.6688 - val_loss: 1.1032 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7343 - loss: 0.5574 - val_accuracy: 0.6803 - val_loss: 0.9028 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.7310 - loss: 0.5579 - val_accuracy: 0.6607 - val_loss: 0.8101 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7143 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7370 - loss: 0.5489 - val_accuracy: 0.6020 - val_loss: 0.9728 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7074 - loss: 0.5625 - val_accuracy: 0.6884 - val_loss: 0.7838 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7227 - loss: 0.5566 - val_accuracy: 0.4502 - val_loss: 2.1539 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7109 - loss: 0.5828 - val_accuracy: 0.6542 - val_loss: 1.4525 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7215 - loss: 0.5459 - val_accuracy: 0.6607 - val_loss: 1.3602 - learning_rate: 0.0010
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7208 - loss: 0.5558 - val_accuracy: 0.6525 - val_loss: 1.4265 - learning_rate: 0.0010
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6948 - loss: 0.5

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7147 - loss: 0.5518 - val_accuracy: 0.6900 - val_loss: 0.8252 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7087 - loss: 0.5621 - val_accuracy: 0.6884 - val_loss: 0.8264 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7076 - loss: 0.5644 - val_accuracy: 0.6966 - val_loss: 0.8008 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7193 - loss: 0.5579 - val_accuracy: 0.6982 - val_loss: 0.7796 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7072 - loss: 0.5443 - val_accuracy: 0.7015 - val_loss: 0.7694 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6968 - loss: 0.5844 - val_accuracy: 0.7015 - val_loss: 0.7732 - learning_rate: 1.0000e-04
Epoch 1819/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7201 - loss: 0.5519 - val_accuracy: 0.6835 - val_loss: 0.8775 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6864 - loss: 0.5725 - val_accuracy: 0.6933 - val_loss: 0.8142 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.7237 - loss: 0.5503 - val_accuracy: 0.6900 - val_loss: 0.8262 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6986 - loss: 0.5745 - val_accuracy: 0.6982 - val_loss: 0.7797 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7110 - loss: 0.5501 - val_accuracy: 0.6949 - val_loss: 0.7939 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6825 - loss: 0.5784 - val_accuracy: 0.6835 - val_loss: 0.8660 - learning_rate: 1.0000e-04
Epoch 1861/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6973 - loss: 0.5708 - val_accuracy: 0.6966 - val_loss: 0.7978 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6645 - loss: 0.5883 - val_accuracy: 0.6982 - val_loss: 0.8116 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6841 - loss: 0.5894 - val_accuracy: 0.6949 - val_loss: 0.7914 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7161 - loss: 0.5596 - val_accuracy: 0.6819 - val_loss: 0.8373 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7174 - loss: 0.5516 - val_accuracy: 0.6966 - val_loss: 0.8010 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7186 - loss: 0.5407 - val_accuracy: 0.7015 - val_loss: 0.7791 - learning_rate: 1.0000e-04
Epoch 1903/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7113 - loss: 0.5542 - val_accuracy: 0.6966 - val_loss: 0.7980 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7100 - loss: 0.5572 - val_accuracy: 0.6835 - val_loss: 0.8408 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7037 - loss: 0.5626 - val_accuracy: 0.6917 - val_loss: 0.8211 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7088 - loss: 0.5475 - val_accuracy: 0.7080 - val_loss: 0.7512 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7014 - loss: 0.5526 - val_accuracy: 0.6949 - val_loss: 0.7790 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6982 - loss: 0.5549 - val_accuracy: 0.6949 - val_loss: 0.8020 - learning_rate: 1.0000e-04
Epoch 1945/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7046 - loss: 0.5550 - val_accuracy: 0.6982 - val_loss: 0.8087 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7080 - loss: 0.5647 - val_accuracy: 0.6966 - val_loss: 0.7989 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7139 - loss: 0.5473 - val_accuracy: 0.6835 - val_loss: 0.8666 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6859 - loss: 0.5937 - val_accuracy: 0.6949 - val_loss: 0.7887 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7210 - loss: 0.5951 - val_accuracy: 0.6835 - val_loss: 0.8300 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6948 - loss: 0.5790 - val_accuracy: 0.6966 - val_loss: 0.7804 - learning_rate: 1.0000e-04
Epoch 1987/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step 

In [12]:
#FCN-XI

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
#    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('linear')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('linear')(conv2)
    

    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.Activation('linear')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv3)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist11 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log11 = pd.DataFrame(hist11.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering fcn_model11
fcn_model11 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 6s 47ms/step - accuracy: 0.5301 - loss: 0.6942 - val_accuracy: 0.4437 - val_loss: 0.8177 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.5310 - loss: 0.7019 - val_accuracy: 0.3801 - val_loss: 1.1446 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.5497 - loss: 0.6799 - val_accuracy: 0.3801 - val_loss: 1.4611 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.5474 - loss: 0.6828 - val_accuracy: 0.5220 - val_loss: 0.7554 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6751 - loss: 0.6423 - val_accuracy: 0.6297 - val_loss: 1.2104 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.6916 - loss: 0.6129 - val_accuracy: 0.6248 - val_loss: 3.4326 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6923 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7104 - loss: 0.5989 - val_accuracy: 0.6509 - val_loss: 1.3520 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7001 - loss: 0.5792 - val_accuracy: 0.6362 - val_loss: 0.8499 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7152 - loss: 0.5562 - val_accuracy: 0.6966 - val_loss: 0.7024 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7330 - loss: 0.5614 - val_accuracy: 0.6281 - val_loss: 2.7112 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6986 - loss: 0.6023 - val_accuracy: 0.6639 - val_loss: 1.2504 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7130 - loss: 0.5681 - val_accuracy: 0.6917 - val_loss: 0.7321 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7063 - loss: 0.5680 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7004 - loss: 0.5695 - val_accuracy: 0.6444 - val_loss: 1.6937 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7216 - loss: 0.5545 - val_accuracy: 0.6705 - val_loss: 0.7615 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6779 - loss: 0.5794 - val_accuracy: 0.6770 - val_loss: 1.0103 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7055 - loss: 0.5689 - val_accuracy: 0.6639 - val_loss: 1.0566 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7133 - loss: 0.5583 - val_accuracy: 0.6705 - val_loss: 1.0622 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7204 - loss: 0.5672 - val_accuracy: 0.6737 - val_loss: 0.8387 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7014 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7048 - loss: 0.5780 - val_accuracy: 0.7047 - val_loss: 0.7284 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7171 - loss: 0.5848 - val_accuracy: 0.6623 - val_loss: 0.7988 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6597 - loss: 0.6197 - val_accuracy: 0.6607 - val_loss: 0.8375 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7479 - loss: 0.5467 - val_accuracy: 0.6852 - val_loss: 0.7925 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6757 - loss: 0.6080 - val_accuracy: 0.7129 - val_loss: 0.6988 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6864 - loss: 0.6006 - val_accuracy: 0.7047 - val_loss: 0.7343 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7115 - loss: 0.5

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7477 - loss: 0.5438 - val_accuracy: 0.6623 - val_loss: 1.0315 - learning_rate: 0.0010
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7068 - loss: 0.5659 - val_accuracy: 0.7015 - val_loss: 0.6964 - learning_rate: 0.0010
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7084 - loss: 0.5782 - val_accuracy: 0.6558 - val_loss: 1.2579 - learning_rate: 0.0010
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7148 - loss: 0.5610 - val_accuracy: 0.6819 - val_loss: 0.8529 - learning_rate: 0.0010
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7119 - loss: 0.5472 - val_accuracy: 0.6819 - val_loss: 0.8359 - learning_rate: 5.0000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7188 - loss: 0.5642 - val_accuracy: 0.7113 - val_loss: 0.7234 - learning_rate: 5.0000e-04
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7282 - l

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7263 - loss: 0.5656 - val_accuracy: 0.6966 - val_loss: 0.7879 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7100 - loss: 0.5676 - val_accuracy: 0.6884 - val_loss: 0.8271 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7282 - loss: 0.5402 - val_accuracy: 0.6982 - val_loss: 0.7790 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7102 - loss: 0.5368 - val_accuracy: 0.6949 - val_loss: 0.8173 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7047 - loss: 0.5789 - val_accuracy: 0.6982 - val_loss: 0.7783 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6940 - loss: 0.5878 - val_accuracy: 0.6900 - val_loss: 0.8150 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7137 - loss: 0.5837 - val_accuracy: 0.6900 - val_loss: 0.8205 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7283 - loss: 0.5451 - val_accuracy: 0.6949 - val_loss: 0.7873 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7070 - loss: 0.5684 - val_accuracy: 0.6803 - val_loss: 0.8330 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7269 - loss: 0.5380 - val_accuracy: 0.6835 - val_loss: 0.8654 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6715 - loss: 0.5772 - val_accuracy: 0.6966 - val_loss: 0.7778 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7228 - loss: 0.5447 - val_accuracy: 0.6835 - val_loss: 0.8583 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.7216 - loss: 0.5483 - val_accuracy: 0.6982 - val_loss: 0.7788 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6952 - loss: 0.6038 - val_accuracy: 0.6966 - val_loss: 0.7942 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7254 - loss: 0.5364 - val_accuracy: 0.6966 - val_loss: 0.7827 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6835 - loss: 0.5891 - val_accuracy: 0.6966 - val_loss: 0.7916 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6766 - loss: 0.5916 - val_accuracy: 0.6966 - val_loss: 0.8100 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.6837 - loss: 0.6055 - val_accuracy: 0.6966 - val_loss: 0.7814 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6936 - loss: 0.5514 - val_accuracy: 0.7031 - val_loss: 0.7634 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7212 - loss: 0.5485 - val_accuracy: 0.6835 - val_loss: 0.8433 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 38ms/step - accuracy: 0.7098 - loss: 0.5399 - val_accuracy: 0.6966 - val_loss: 0.7847 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7116 - loss: 0.5530 - val_accuracy: 0.6966 - val_loss: 0.8032 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6950 - loss: 0.5702 - val_accuracy: 0.6933 - val_loss: 0.7793 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7312 - loss: 0.5566 - val_accuracy: 0.6966 - val_loss: 0.7957 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7356 - loss: 0.5414 - val_accuracy: 0.6966 - val_loss: 0.8084 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7066 - loss: 0.5417 - val_accuracy: 0.6933 - val_loss: 0.7898 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7088 - loss: 0.5618 - val_accuracy: 0.7031 - val_loss: 0.7547 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7197 - loss: 0.5460 - val_accuracy: 0.6835 - val_loss: 0.8905 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7376 - loss: 0.5304 - val_accuracy: 0.6966 - val_loss: 0.7791 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6754 - loss: 0.5858 - val_accuracy: 0.6835 - val_loss: 0.8602 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step 

In [13]:
#FCN-XII

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
#    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('linear')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('linear')(conv2)
    

    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.Activation('linear')(conv3)


    conv4 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv3)
#    conv4 = keras.layers.BatchNormalization()(conv4)
    conv4 = keras.layers.Activation('linear')(conv4)
    
    full = keras.layers.GlobalAveragePooling2D()(conv4)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist12 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log12 = pd.DataFrame(hist12.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering 
fcn_model12 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 5s 42ms/step - accuracy: 0.5440 - loss: 0.6858 - val_accuracy: 0.3801 - val_loss: 1.9044 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.5522 - loss: 0.6844 - val_accuracy: 0.6199 - val_loss: 0.6643 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.5384 - loss: 0.6830 - val_accuracy: 0.3964 - val_loss: 1.3960 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6372 - loss: 0.6465 - val_accuracy: 0.6199 - val_loss: 1.4879 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6633 - loss: 0.6403 - val_accuracy: 0.4095 - val_loss: 2.5877 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6804 - loss: 0.5997 - val_accuracy: 0.6378 - val_loss: 0.6972 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6927 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6957 - loss: 0.5956 - val_accuracy: 0.6770 - val_loss: 0.8625 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7448 - loss: 0.5454 - val_accuracy: 0.6786 - val_loss: 0.9117 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6737 - loss: 0.5714 - val_accuracy: 0.4845 - val_loss: 1.4697 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7253 - loss: 0.5703 - val_accuracy: 0.6395 - val_loss: 0.8718 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7368 - loss: 0.5657 - val_accuracy: 0.6933 - val_loss: 0.6440 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6908 - loss: 0.5881 - val_accuracy: 0.6884 - val_loss: 0.7853 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7206 - loss: 0.5811 - 

Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7169 - loss: 0.5712 - val_accuracy: 0.6330 - val_loss: 2.1175 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6932 - loss: 0.6120 - val_accuracy: 0.7080 - val_loss: 0.7117 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7200 - loss: 0.5490 - val_accuracy: 0.6427 - val_loss: 1.2008 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7045 - loss: 0.5927 - val_accuracy: 0.6688 - val_loss: 1.1380 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7328 - loss: 0.5481 - val_accuracy: 0.6476 - val_loss: 1.1866 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7383 - loss: 0.5727 - val_accuracy: 0.6476 - val_loss: 1.5550 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7107 - l

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7093 - loss: 0.5424 - val_accuracy: 0.7096 - val_loss: 0.7136 - learning_rate: 5.0000e-04
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7113 - loss: 0.5721 - val_accuracy: 0.6770 - val_loss: 0.9636 - learning_rate: 5.0000e-04
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7485 - loss: 0.5378 - val_accuracy: 0.6949 - val_loss: 0.7710 - learning_rate: 5.0000e-04
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6832 - loss: 0.5860 - val_accuracy: 0.7113 - val_loss: 0.7297 - learning_rate: 5.0000e-04
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7125 - loss: 0.5784 - val_accuracy: 0.6982 - val_loss: 0.7338 - learning_rate: 5.0000e-04
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7127 - loss: 0.5660 - val_accuracy: 0.7031 - val_loss: 0.7427 - learning_rate: 5.0000e-04
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accu

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7133 - loss: 0.5661 - val_accuracy: 0.6966 - val_loss: 0.7724 - learning_rate: 2.5000e-04
Epoch 174/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7181 - loss: 0.5377 - val_accuracy: 0.7113 - val_loss: 0.7314 - learning_rate: 2.5000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7148 - loss: 0.5556 - val_accuracy: 0.6852 - val_loss: 0.8226 - learning_rate: 2.5000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7116 - loss: 0.5442 - val_accuracy: 0.7096 - val_loss: 0.7350 - learning_rate: 2.5000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7034 - loss: 0.5597 - val_accuracy: 0.7064 - val_loss: 0.7429 - learning_rate: 2.5000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7158 - loss: 0.5639 - val_accuracy: 0.6884 - val_loss: 0.8085 - learning_rate: 2.5000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accu

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7044 - loss: 0.5612 - val_accuracy: 0.6966 - val_loss: 0.7832 - learning_rate: 1.0000e-04
Epoch 1812/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7030 - loss: 0.5401 - val_accuracy: 0.6949 - val_loss: 0.7901 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6999 - loss: 0.5532 - val_accuracy: 0.6949 - val_loss: 0.7780 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6692 - loss: 0.5921 - val_accuracy: 0.6868 - val_loss: 0.8393 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.6991 - loss: 0.5533 - val_accuracy: 0.7031 - val_loss: 0.7607 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7315 - loss: 0.5588 - val_accuracy: 0.6966 - val_loss: 0.7939 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7295 - loss: 0.5445 - val_accuracy: 0.6966 - val_loss: 0.8080 - learning_rate: 1.0000e-04
Epoch 1854/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6878 - loss: 0.5828 - val_accuracy: 0.6966 - val_loss: 0.7886 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7190 - loss: 0.5662 - val_accuracy: 0.6819 - val_loss: 0.8351 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7223 - loss: 0.5457 - val_accuracy: 0.7015 - val_loss: 0.7684 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6913 - loss: 0.5772 - val_accuracy: 0.6966 - val_loss: 0.7808 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7079 - loss: 0.5582 - val_accuracy: 0.6966 - val_loss: 0.8043 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6814 - loss: 0.5685 - val_accuracy: 0.6966 - val_loss: 0.8036 - learning_rate: 1.0000e-04
Epoch 1896/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7189 - loss: 0.5421 - val_accuracy: 0.6835 - val_loss: 0.8801 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7117 - loss: 0.5513 - val_accuracy: 0.7031 - val_loss: 0.7570 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7220 - loss: 0.5431 - val_accuracy: 0.6949 - val_loss: 0.7848 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7001 - loss: 0.5697 - val_accuracy: 0.6884 - val_loss: 0.8159 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7190 - loss: 0.5336 - val_accuracy: 0.6966 - val_loss: 0.8133 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7124 - loss: 0.5297 - val_accuracy: 0.6917 - val_loss: 0.8210 - learning_rate: 1.0000e-04
Epoch 1938/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7306 - loss: 0.5521 - val_accuracy: 0.7015 - val_loss: 0.7610 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7002 - loss: 0.5831 - val_accuracy: 0.6949 - val_loss: 0.7884 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7195 - loss: 0.5491 - val_accuracy: 0.7031 - val_loss: 0.7758 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7307 - loss: 0.5423 - val_accuracy: 0.7031 - val_loss: 0.7722 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6973 - loss: 0.5630 - val_accuracy: 0.6949 - val_loss: 0.7850 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6932 - loss: 0.5482 - val_accuracy: 0.7015 - val_loss: 0.7668 - learning_rate: 1.0000e-04
Epoch 1980/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7172 - loss: 0.5683 - val_accuracy: 0.6852 - val_loss: 0.8576 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6901 - loss: 0.5692 - val_accuracy: 0.6966 - val_loss: 0.7781 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6998 - loss: 0.5694 - val_accuracy: 0.6900 - val_loss: 0.8203 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6924 - loss: 0.5772 - val_accuracy: 0.6966 - val_loss: 0.7945 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7098 - loss: 0.5855 - val_accuracy: 0.6966 - val_loss: 0.7814 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step 

In [14]:
#FCN-XIII

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('linear')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
#    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
#    conv2 = keras.layers.BatchNormalization()(conv2)
#    conv2 = keras.layers.Activation('linear')(conv2)
    
#    drop_out = Dropout(0.2)(conv2)
#    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
#    conv3 = keras.layers.Activation('linear')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv1)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist13 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
    log13 = pd.DataFrame(hist13.history)
 #   print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering 
fcn_model13 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 3s 24ms/step - accuracy: 0.5306 - loss: 0.7628 - val_accuracy: 0.6199 - val_loss: 0.6633 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6178 - loss: 0.6713 - val_accuracy: 0.6199 - val_loss: 0.7145 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6084 - loss: 0.6571 - val_accuracy: 0.6199 - val_loss: 0.6559 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6464 - loss: 0.6379 - val_accuracy: 0.6705 - val_loss: 0.6597 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6616 - loss: 0.6262 - val_accuracy: 0.6199 - val_loss: 0.6653 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6153 - loss: 0.6803 - val_accuracy: 0.6199 - val_loss: 1.0893 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6182 - loss: 0.66

Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6347 - loss: 0.6191 - val_accuracy: 0.6199 - val_loss: 3.4667 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.6412 - loss: 0.6331 - val_accuracy: 0.6721 - val_loss: 0.6990 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6611 - loss: 0.6050 - val_accuracy: 0.4845 - val_loss: 1.2527 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6771 - loss: 0.5940 - val_accuracy: 0.5938 - val_loss: 0.8099 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6975 - loss: 0.5912 - val_accuracy: 0.6346 - val_loss: 1.6068 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6792 - loss: 0.6118 - val_accuracy: 0.6558 - val_loss: 0.8567 - learning_rate: 0.0010
Epoch 51/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7016 - los

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6817 - loss: 0.5979 - val_accuracy: 0.3883 - val_loss: 4.1535 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.6518 - loss: 0.6141 - val_accuracy: 0.6852 - val_loss: 0.6912 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7200 - loss: 0.5743 - val_accuracy: 0.6509 - val_loss: 1.2131 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7123 - loss: 0.5822 - val_accuracy: 0.3834 - val_loss: 5.5682 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6586 - loss: 0.6142 - val_accuracy: 0.6639 - val_loss: 0.8329 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - accuracy: 0.7123 - loss: 0.5778 - val_accuracy: 0.6623 - val_loss: 0.8822 - learning_rate: 0.0010
Epoch 94/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - accuracy: 0.7188 - loss: 0.5834 - v

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7225 - loss: 0.5973 - val_accuracy: 0.6248 - val_loss: 2.8835 - learning_rate: 0.0010
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7016 - loss: 0.5740 - val_accuracy: 0.6786 - val_loss: 0.7594 - learning_rate: 0.0010
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6975 - loss: 0.5988 - val_accuracy: 0.4633 - val_loss: 1.5917 - learning_rate: 0.0010
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.6494 - loss: 0.6100 - val_accuracy: 0.6411 - val_loss: 1.6359 - learning_rate: 0.0010
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7251 - loss: 0.5605 - val_accuracy: 0.4878 - val_loss: 1.3798 - learning_rate: 0.0010
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step - accuracy: 0.6581 - loss: 0.5868 - val_accuracy: 0.6835 - val_loss: 0.6916 - learning_rate: 0.0010
Epoch 137/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6940 - loss: 0.5847

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7143 - loss: 0.5784 - val_accuracy: 0.6395 - val_loss: 1.7752 - learning_rate: 5.0000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6862 - loss: 0.6071 - val_accuracy: 0.4307 - val_loss: 2.3584 - learning_rate: 5.0000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6954 - loss: 0.5811 - val_accuracy: 0.6688 - val_loss: 0.8199 - learning_rate: 5.0000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7102 - loss: 0.5705 - val_accuracy: 0.6982 - val_loss: 0.6782 - learning_rate: 5.0000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.6973 - loss: 0.5946 - val_accuracy: 0.7096 - val_loss: 0.6814 - learning_rate: 5.0000e-04
Epoch 179/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.6923 - loss: 0.5962 - val_accuracy: 0.5710 - val_loss: 0.9699 - learning_rate: 5.0000e-04
Epoch 180/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accurac

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - accuracy: 0.7304 - loss: 0.5699 - val_accuracy: 0.6868 - val_loss: 0.7897 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7277 - loss: 0.5807 - val_accuracy: 0.6754 - val_loss: 0.9044 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 11ms/step - accuracy: 0.7231 - loss: 0.5721 - val_accuracy: 0.6884 - val_loss: 0.8118 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step - accuracy: 0.7190 - loss: 0.5712 - val_accuracy: 0.7080 - val_loss: 0.6898 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7264 - loss: 0.5590 - val_accuracy: 0.7096 - val_loss: 0.6869 - learning_rate: 1.0000e-04
Epoch 1817/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7197 - loss: 0.5732 - val_accuracy: 0.6819 - val_loss: 0.8224 - learning_rate: 1.0000e-04
Epoch 1818/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step -

37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.7262 - loss: 0.5718 - val_accuracy: 0.7129 - val_loss: 0.6839 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7060 - loss: 0.5623 - val_accuracy: 0.7031 - val_loss: 0.7065 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 16ms/step - accuracy: 0.6925 - loss: 0.5797 - val_accuracy: 0.6721 - val_loss: 0.9637 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7041 - loss: 0.5803 - val_accuracy: 0.6982 - val_loss: 0.7455 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 9ms/step - accuracy: 0.6915 - loss: 0.5645 - val_accuracy: 0.7064 - val_loss: 0.6806 - learning_rate: 1.0000e-04
Epoch 1859/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.6824 - loss: 0.5892 - val_accuracy: 0.6803 - val_loss: 0.8486 - learning_rate: 1.0000e-04
Epoch 1860/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 14ms/step - accuracy: 0.7127 - loss: 0.5878 - val_accuracy: 0.6884 - val_loss: 0.8071 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7165 - loss: 0.5701 - val_accuracy: 0.7080 - val_loss: 0.6791 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 8ms/step - accuracy: 0.7149 - loss: 0.5677 - val_accuracy: 0.6819 - val_loss: 0.8232 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - accuracy: 0.6725 - loss: 0.6118 - val_accuracy: 0.6835 - val_loss: 0.8200 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 15ms/step - accuracy: 0.7326 - loss: 0.5350 - val_accuracy: 0.7096 - val_loss: 0.6953 - learning_rate: 1.0000e-04
Epoch 1901/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7105 - loss: 0.5744 - val_accuracy: 0.6803 - val_loss: 0.8269 - learning_rate: 1.0000e-04
Epoch 1902/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 10ms/step -

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7046 - loss: 0.5782 - val_accuracy: 0.6900 - val_loss: 0.8055 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7024 - loss: 0.5818 - val_accuracy: 0.7096 - val_loss: 0.6784 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - accuracy: 0.7342 - loss: 0.5420 - val_accuracy: 0.6786 - val_loss: 0.8479 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 12ms/step - accuracy: 0.6800 - loss: 0.5986 - val_accuracy: 0.7096 - val_loss: 0.6868 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7023 - loss: 0.5734 - val_accuracy: 0.6639 - val_loss: 1.0427 - learning_rate: 1.0000e-04
Epoch 1943/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - accuracy: 0.7121 - loss: 0.5711 - val_accuracy: 0.7096 - val_loss: 0.6961 - learning_rate: 1.0000e-04
Epoch 1944/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 11ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7083 - loss: 0.5807 - val_accuracy: 0.6900 - val_loss: 0.7689 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 10ms/step - accuracy: 0.7108 - loss: 0.5866 - val_accuracy: 0.7096 - val_loss: 0.6881 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 13ms/step - accuracy: 0.7298 - loss: 0.5615 - val_accuracy: 0.6900 - val_loss: 0.7310 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 13ms/step - accuracy: 0.7182 - loss: 0.5828 - val_accuracy: 0.6803 - val_loss: 0.8474 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7174 - loss: 0.5642 - val_accuracy: 0.7113 - val_loss: 0.6920 - learning_rate: 1.0000e-04
Epoch 1985/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step - accuracy: 0.7436 - loss: 0.5577 - val_accuracy: 0.7113 - val_loss: 0.6790 - learning_rate: 1.0000e-04
Epoch 1986/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 0s 12ms/step 

In [15]:
#FCN-XIV

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('linear')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('linear')(conv2)
    
#    drop_out = Dropout(0.2)(conv2)
#    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
#    conv3 = keras.layers.BatchNormalization()(conv3)
#    conv3 = keras.layers.Activation('linear')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv2)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist14 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log14 = pd.DataFrame(hist14.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
fcn_model14 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 7s 44ms/step - accuracy: 0.4910 - loss: 2.2863 - val_accuracy: 0.6199 - val_loss: 0.8453 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6504 - loss: 0.6320 - val_accuracy: 0.6199 - val_loss: 0.6991 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6377 - loss: 0.6579 - val_accuracy: 0.6264 - val_loss: 0.6432 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6597 - loss: 0.6178 - val_accuracy: 0.6199 - val_loss: 1.0833 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6642 - loss: 0.6202 - val_accuracy: 0.6199 - val_loss: 0.8051 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6542 - loss: 0.6215 - val_accuracy: 0.6493 - val_loss: 0.6199 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6726 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6328 - loss: 0.6544 - val_accuracy: 0.6199 - val_loss: 8.4955 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7035 - loss: 0.5886 - val_accuracy: 0.6542 - val_loss: 1.6437 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7293 - loss: 0.5544 - val_accuracy: 0.3801 - val_loss: 9.0105 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6570 - loss: 0.6158 - val_accuracy: 0.6395 - val_loss: 1.9226 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7111 - loss: 0.5800 - val_accuracy: 0.3997 - val_loss: 3.2667 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7137 - loss: 0.5715 - val_accuracy: 0.3817 - val_loss: 7.7238 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6926 - loss: 0.5805 - 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7141 - loss: 0.5736 - val_accuracy: 0.6542 - val_loss: 1.4147 - learning_rate: 5.0000e-04
Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7241 - loss: 0.5405 - val_accuracy: 0.6460 - val_loss: 1.8153 - learning_rate: 5.0000e-04
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6723 - loss: 0.5844 - val_accuracy: 0.6346 - val_loss: 2.1708 - learning_rate: 5.0000e-04
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6844 - loss: 0.6033 - val_accuracy: 0.6476 - val_loss: 1.6622 - learning_rate: 5.0000e-04
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7222 - loss: 0.5610 - val_accuracy: 0.3817 - val_loss: 5.9688 - learning_rate: 5.0000e-04
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 23ms/step - accuracy: 0.6944 - loss: 0.5823 - val_accuracy: 0.3915 - val_loss: 4.5411 - learning_rate: 5.0000e-04
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.7032 - loss: 0.5685 - val_accuracy: 0.3817 - val_loss: 7.5025 - learning_rate: 5.0000e-04
Epoch 130/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6871 - loss: 0.5927 - val_accuracy: 0.6591 - val_loss: 0.8597 - learning_rate: 5.0000e-04
Epoch 131/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7263 - loss: 0.5528 - val_accuracy: 0.6852 - val_loss: 0.9138 - learning_rate: 5.0000e-04
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7045 - loss: 0.5798 - val_accuracy: 0.6803 - val_loss: 0.7616 - learning_rate: 5.0000e-04
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6671 - loss: 0.5915 - val_accuracy: 0.5139 - val_loss: 1.3902 - learning_rate: 5.0000e-04
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7326 - loss: 0.5558 - val_accuracy: 0.6183 - val_loss: 5.3477 - learning_rate: 5.0000e-04
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accu

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7095 - loss: 0.6054 - val_accuracy: 0.6427 - val_loss: 1.8891 - learning_rate: 5.0000e-04
Epoch 172/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7270 - loss: 0.5711 - val_accuracy: 0.6330 - val_loss: 0.9267 - learning_rate: 2.5000e-04
Epoch 173/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7059 - loss: 0.5725 - val_accuracy: 0.3883 - val_loss: 5.3421 - learning_rate: 2.5000e-04
Epoch 174/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7272 - loss: 0.5393 - val_accuracy: 0.5530 - val_loss: 1.2169 - learning_rate: 2.5000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7259 - loss: 0.5400 - val_accuracy: 0.4078 - val_loss: 3.5311 - learning_rate: 2.5000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7279 - loss: 0.5606 - val_accuracy: 0.6982 - val_loss: 0.7315 - learning_rate: 2.5000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accu

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6790 - loss: 0.5942 - val_accuracy: 0.6688 - val_loss: 1.0971 - learning_rate: 1.0000e-04
Epoch 1810/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7003 - loss: 0.5695 - val_accuracy: 0.6574 - val_loss: 1.4310 - learning_rate: 1.0000e-04
Epoch 1811/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7040 - loss: 0.5688 - val_accuracy: 0.7129 - val_loss: 0.7173 - learning_rate: 1.0000e-04
Epoch 1812/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6793 - loss: 0.5670 - val_accuracy: 0.6395 - val_loss: 2.0590 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7110 - loss: 0.5704 - val_accuracy: 0.6949 - val_loss: 0.7951 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7208 - loss: 0.5636 - val_accuracy: 0.4878 - val_loss: 1.5488 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7197 - loss: 0.5356 - val_accuracy: 0.6607 - val_loss: 0.8101 - learning_rate: 1.0000e-04
Epoch 1852/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7079 - loss: 0.5754 - val_accuracy: 0.7096 - val_loss: 0.7262 - learning_rate: 1.0000e-04
Epoch 1853/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6991 - loss: 0.5922 - val_accuracy: 0.4600 - val_loss: 2.0864 - learning_rate: 1.0000e-04
Epoch 1854/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7013 - loss: 0.5878 - val_accuracy: 0.7031 - val_loss: 0.7301 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7194 - loss: 0.5535 - val_accuracy: 0.6884 - val_loss: 0.8714 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7207 - loss: 0.5618 - val_accuracy: 0.6917 - val_loss: 0.7699 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7516 - loss: 0.5513 - val_accuracy: 0.7113 - val_loss: 0.7211 - learning_rate: 1.0000e-04
Epoch 1894/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7030 - loss: 0.5798 - val_accuracy: 0.6362 - val_loss: 2.2692 - learning_rate: 1.0000e-04
Epoch 1895/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7178 - loss: 0.5736 - val_accuracy: 0.6688 - val_loss: 1.0949 - learning_rate: 1.0000e-04
Epoch 1896/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7227 - loss: 0.5618 - val_accuracy: 0.6476 - val_loss: 0.8934 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7121 - loss: 0.5599 - val_accuracy: 0.7031 - val_loss: 0.7364 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6864 - loss: 0.5760 - val_accuracy: 0.4910 - val_loss: 1.5761 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7191 - loss: 0.5780 - val_accuracy: 0.6770 - val_loss: 0.9704 - learning_rate: 1.0000e-04
Epoch 1936/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7064 - loss: 0.5524 - val_accuracy: 0.6852 - val_loss: 0.8460 - learning_rate: 1.0000e-04
Epoch 1937/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6852 - loss: 0.5749 - val_accuracy: 0.6819 - val_loss: 0.9191 - learning_rate: 1.0000e-04
Epoch 1938/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6852 - loss: 0.5791 - val_accuracy: 0.7015 - val_loss: 0.7640 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7173 - loss: 0.5573 - val_accuracy: 0.6803 - val_loss: 1.0179 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6911 - loss: 0.5623 - val_accuracy: 0.6949 - val_loss: 0.8167 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6918 - loss: 0.6079 - val_accuracy: 0.6444 - val_loss: 1.8783 - learning_rate: 1.0000e-04
Epoch 1978/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7302 - loss: 0.5742 - val_accuracy: 0.6835 - val_loss: 0.8351 - learning_rate: 1.0000e-04
Epoch 1979/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6878 - loss: 0.5800 - val_accuracy: 0.6542 - val_loss: 1.4949 - learning_rate: 1.0000e-04
Epoch 1980/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7071 - loss: 0.5693 - val_accuracy: 0.6427 - val_loss: 1.7981 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7122 - loss: 0.5638 - val_accuracy: 0.6199 - val_loss: 0.9253 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6941 - loss: 0.5724 - val_accuracy: 0.6444 - val_loss: 1.8802 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step 

In [16]:
#FCN-XV

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('linear')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('linear')(conv2)
    

    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.Activation('linear')(conv3)
    
    full = keras.layers.GlobalAveragePooling2D()(conv3)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist15 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log15 = pd.DataFrame(hist15.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
fcn_model15 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 10s 53ms/step - accuracy: 0.5014 - loss: 1.1647 - val_accuracy: 0.3801 - val_loss: 1.7750 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.6113 - loss: 0.6582 - val_accuracy: 0.3801 - val_loss: 1.2480 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.6469 - loss: 0.6335 - val_accuracy: 0.5285 - val_loss: 0.6954 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.6816 - loss: 0.6154 - val_accuracy: 0.6199 - val_loss: 0.8045 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6679 - loss: 0.6108 - val_accuracy: 0.6199 - val_loss: 3.0039 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6975 - loss: 0.5713 - val_accuracy: 0.6199 - val_loss: 0.7531 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 36ms/step - accuracy: 0.6481 - loss: 0

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.6788 - loss: 0.6451 - val_accuracy: 0.3964 - val_loss: 5.1068 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6719 - loss: 0.6023 - val_accuracy: 0.5302 - val_loss: 1.3507 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6916 - loss: 0.6132 - val_accuracy: 0.4861 - val_loss: 1.5130 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 2s 42ms/step - accuracy: 0.6959 - loss: 0.6044 - val_accuracy: 0.7113 - val_loss: 0.6984 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.6768 - loss: 0.5986 - val_accuracy: 0.6199 - val_loss: 11.8302 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6673 - loss: 0.6137 - val_accuracy: 0.3801 - val_loss: 17.7065 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6798 - loss: 0.5981 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy: 0.7106 - loss: 0.5741 - val_accuracy: 0.6199 - val_loss: 10.6764 - learning_rate: 5.0000e-04
Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6908 - loss: 0.5969 - val_accuracy: 0.6199 - val_loss: 4.4208 - learning_rate: 5.0000e-04
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.6565 - loss: 0.6094 - val_accuracy: 0.6199 - val_loss: 4.2183 - learning_rate: 5.0000e-04
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6723 - loss: 0.6041 - val_accuracy: 0.6264 - val_loss: 2.8009 - learning_rate: 5.0000e-04
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.6866 - loss: 0.5867 - val_accuracy: 0.6591 - val_loss: 1.3207 - learning_rate: 5.0000e-04
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7581 - loss: 0.5287 - val_accuracy: 0.6754 - val_loss: 0.9528 - learning_rate: 5.0000e-04
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accuracy:

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7039 - loss: 0.5942 - val_accuracy: 0.6199 - val_loss: 3.7840 - learning_rate: 5.0000e-04
Epoch 130/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7080 - loss: 0.5720 - val_accuracy: 0.6199 - val_loss: 3.6561 - learning_rate: 5.0000e-04
Epoch 131/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.7528 - loss: 0.5423 - val_accuracy: 0.3801 - val_loss: 8.1615 - learning_rate: 5.0000e-04
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.7266 - loss: 0.5546 - val_accuracy: 0.6199 - val_loss: 3.7710 - learning_rate: 5.0000e-04
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7159 - loss: 0.5855 - val_accuracy: 0.6183 - val_loss: 5.6838 - learning_rate: 5.0000e-04
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7032 - loss: 0.5815 - val_accuracy: 0.6199 - val_loss: 5.1475 - learning_rate: 5.0000e-04
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accu

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.7021 - loss: 0.5690 - val_accuracy: 0.6639 - val_loss: 0.7853 - learning_rate: 2.5000e-04
Epoch 172/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7317 - loss: 0.5671 - val_accuracy: 0.6444 - val_loss: 1.6620 - learning_rate: 2.5000e-04
Epoch 173/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7057 - loss: 0.5625 - val_accuracy: 0.6623 - val_loss: 1.3369 - learning_rate: 2.5000e-04
Epoch 174/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 32ms/step - accuracy: 0.7000 - loss: 0.5848 - val_accuracy: 0.6819 - val_loss: 0.9789 - learning_rate: 2.5000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 33ms/step - accuracy: 0.7038 - loss: 0.5749 - val_accuracy: 0.3801 - val_loss: 8.8345 - learning_rate: 2.5000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 34ms/step - accuracy: 0.6952 - loss: 0.5834 - val_accuracy: 0.7047 - val_loss: 0.7045 - learning_rate: 2.5000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 35ms/step - accu

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7067 - loss: 0.5766 - val_accuracy: 0.6770 - val_loss: 0.9160 - learning_rate: 1.0000e-04
Epoch 1810/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7012 - loss: 0.5672 - val_accuracy: 0.6591 - val_loss: 1.4063 - learning_rate: 1.0000e-04
Epoch 1811/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6944 - loss: 0.5942 - val_accuracy: 0.6607 - val_loss: 1.3012 - learning_rate: 1.0000e-04
Epoch 1812/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7034 - loss: 0.5629 - val_accuracy: 0.6868 - val_loss: 0.8557 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7062 - loss: 0.5883 - val_accuracy: 0.7015 - val_loss: 0.7746 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6775 - loss: 0.5743 - val_accuracy: 0.6754 - val_loss: 0.9612 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7147 - loss: 0.5741 - val_accuracy: 0.6493 - val_loss: 0.8500 - learning_rate: 1.0000e-04
Epoch 1852/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7095 - loss: 0.5556 - val_accuracy: 0.5351 - val_loss: 1.2878 - learning_rate: 1.0000e-04
Epoch 1853/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7106 - loss: 0.5471 - val_accuracy: 0.5563 - val_loss: 1.1632 - learning_rate: 1.0000e-04
Epoch 1854/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6873 - loss: 0.5639 - val_accuracy: 0.6917 - val_loss: 0.7490 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7205 - loss: 0.5590 - val_accuracy: 0.6591 - val_loss: 1.4148 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6824 - loss: 0.5815 - val_accuracy: 0.6493 - val_loss: 1.6623 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7122 - loss: 0.5498 - val_accuracy: 0.6786 - val_loss: 0.9934 - learning_rate: 1.0000e-04
Epoch 1894/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.7322 - loss: 0.5534 - val_accuracy: 0.6786 - val_loss: 1.0288 - learning_rate: 1.0000e-04
Epoch 1895/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7329 - loss: 0.5567 - val_accuracy: 0.5383 - val_loss: 1.3119 - learning_rate: 1.0000e-04
Epoch 1896/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7119 - loss: 0.5549 - val_accuracy: 0.7080 - val_loss: 0.7180 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6831 - loss: 0.5698 - val_accuracy: 0.5465 - val_loss: 1.2517 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6930 - loss: 0.5760 - val_accuracy: 0.6852 - val_loss: 0.8878 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6725 - loss: 0.6118 - val_accuracy: 0.6542 - val_loss: 1.5437 - learning_rate: 1.0000e-04
Epoch 1936/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7132 - loss: 0.5672 - val_accuracy: 0.6770 - val_loss: 0.9428 - learning_rate: 1.0000e-04
Epoch 1937/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6962 - loss: 0.5718 - val_accuracy: 0.6395 - val_loss: 2.1558 - learning_rate: 1.0000e-04
Epoch 1938/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6752 - loss: 0.5846 - val_accuracy: 0.6819 - val_loss: 1.0020 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7174 - loss: 0.5552 - val_accuracy: 0.5693 - val_loss: 1.1200 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.6924 - loss: 0.5821 - val_accuracy: 0.7129 - val_loss: 0.7160 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7178 - loss: 0.5740 - val_accuracy: 0.6933 - val_loss: 0.7769 - learning_rate: 1.0000e-04
Epoch 1978/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7082 - loss: 0.5456 - val_accuracy: 0.6688 - val_loss: 1.0982 - learning_rate: 1.0000e-04
Epoch 1979/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7182 - loss: 0.5673 - val_accuracy: 0.6607 - val_loss: 1.3977 - learning_rate: 1.0000e-04
Epoch 1980/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7293 - loss: 0.5534 - val_accuracy: 0.4796 - val_loss: 1.6930 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6963 - loss: 0.5883 - val_accuracy: 0.7080 - val_loss: 0.7343 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 24ms/step - accuracy: 0.6828 - loss: 0.6161 - val_accuracy: 0.7015 - val_loss: 0.7245 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step 

In [17]:
#FCN-XVI

# %load FCN.py
#!/usr/bin/env python2
"""
Created on Sun Oct 30 20:11:19 2016

@author: stephen
"""
 
from __future__ import print_function
 
from tensorflow import keras
import numpy as np
import pandas as pd

def readucr(filename):
    data = np.loadtxt(filename, delimiter = ',')
    Y = data[:,0]
    X = data[:,1:]
    return X, Y
  
#nb_epochs = 2000


#flist = ['Adiac', 'Beef', 'CBF', 'ChlorineConcentration', 'CinC_ECG_torso', 'Coffee', 'Cricket_X', 'Cricket_Y', 'Cricket_Z', 
#'DiatomSizeReduction', 'ECGFiveDays', 'FaceAll', 'FaceFour', 'FacesUCR', '50words', 'FISH', 'Gun_Point', 'Haptics', 
#'InlineSkate', 'ItalyPowerDemand', 'Lighting2', 'Lighting7', 'MALLAT', 'MedicalImages', 'MoteStrain', 'NonInvasiveFatalECG_Thorax1', 
#'NonInvasiveFatalECG_Thorax2', 'OliveOil', 'OSULeaf', 'SonyAIBORobotSurface', 'SonyAIBORobotSurfaceII', 'StarLightCurves', 'SwedishLeaf', 'Symbols', 
#'synthetic_control', 'Trace', 'TwoLeadECG', 'Two_Patterns', 'uWaveGestureLibrary_X', 'uWaveGestureLibrary_Y', 'uWaveGestureLibrary_Z', 'wafer', 'WordsSynonyms', 'yoga']

flist  = ['Adiac']
for each in flist:
    fname = each
    x_train, y_train = readucr(fname+'/'+fname+'_TRAIN')
    x_test, y_test = readucr(fname+'/'+fname+'_TEST')
    nb_classes = len(np.unique(y_test))
    batch_size = min(x_train.shape[0]/10, 16)
    
    y_train = (y_train - y_train.min())/(y_train.max()-y_train.min())*(nb_classes-1)
    y_test = (y_test - y_test.min())/(y_test.max()-y_test.min())*(nb_classes-1)
    
    
    Y_train = keras.utils.to_categorical(y_train, nb_classes)
    Y_test = keras.utils.to_categorical(y_test, nb_classes)
    
    x_train_mean = x_train.mean()
    x_train_std = x_train.std()
    x_train = (x_train - x_train_mean)/(x_train_std)
     
    x_test = (x_test - x_train_mean)/(x_train_std)
    x_train = x_train.reshape(x_train.shape + (1,1,))
    x_test = x_test.reshape(x_test.shape + (1,1,))

    x = keras.layers.Input(x_train.shape[1:])
#    drop_out = Dropout(0.2)(x)
    conv1 = keras.layers.Conv2D(128, 8, 1, padding='same')(x)
    conv1 = keras.layers.BatchNormalization()(conv1)
    conv1 = keras.layers.Activation('linear')(conv1)
    
#    drop_out = Dropout(0.2)(conv1)
    conv2 = keras.layers.Conv2D(256, 5, 1, padding='same')(conv1)
    conv2 = keras.layers.BatchNormalization()(conv2)
    conv2 = keras.layers.Activation('linear')(conv2)
    

    conv3 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv2)
    conv3 = keras.layers.BatchNormalization()(conv3)
    conv3 = keras.layers.Activation('linear')(conv3)


    conv4 = keras.layers.Conv2D(128, 3, 1, padding='same')(conv3)
    conv4 = keras.layers.BatchNormalization()(conv4)
    conv4 = keras.layers.Activation('linear')(conv4)
    
    full = keras.layers.GlobalAveragePooling2D()(conv4)
    out = keras.layers.Dense(nb_classes, activation='softmax')(full)
    
    
    model = keras.models.Model(inputs=x, outputs=out)
     
    optimizer = keras.optimizers.Adam()
    model.compile(loss='categorical_crossentropy',
                  optimizer=optimizer,
                  metrics=['accuracy'])
     
    reduce_lr = keras.callbacks.ReduceLROnPlateau(monitor = 'loss', factor=0.5,
                      patience=50, min_lr=0.0001) 
#numbering
    hist16 = model.fit(x_train, Y_train, batch_size=16, epochs=nb_epochs,
              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])

#    hist = model.fit(x_train, Y_train, batch_size=batch_size, nb_epoch=nb_epochs,
#              verbose=1, validation_data=(x_test, Y_test), callbacks = [reduce_lr])
    #Print the testing results which has the lowest training loss.
#numbering
    log16 = pd.DataFrame(hist16.history)
  #  print(log.loc[log['loss'].idxmin]['loss'], log.loc[log['loss'].idxmin]['val_acc'])

import os
cur_dir=os.getcwd()
from keras.models import load_model

model_h5_dir = 'save_model/h5'
model_h5_path = os.path.join(cur_dir,model_h5_dir)
model_h5_file = os.path.join(model_h5_path,'fcn_model.h5')
os.makedirs(model_h5_path,exist_ok=True)


model.save(model_h5_file,save_format='h5')
#numbering
fcn_model16 = keras.models.load_model(model_h5_file)

Epoch 1/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 7s 45ms/step - accuracy: 0.5643 - loss: 0.9470 - val_accuracy: 0.6199 - val_loss: 0.6946 - learning_rate: 0.0010
Epoch 2/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 31ms/step - accuracy: 0.6192 - loss: 0.6505 - val_accuracy: 0.6199 - val_loss: 0.7762 - learning_rate: 0.0010
Epoch 3/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7146 - loss: 0.5886 - val_accuracy: 0.6232 - val_loss: 0.6516 - learning_rate: 0.0010
Epoch 4/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6854 - loss: 0.6303 - val_accuracy: 0.3948 - val_loss: 1.1010 - learning_rate: 0.0010
Epoch 5/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6883 - loss: 0.6102 - val_accuracy: 0.6313 - val_loss: 0.6344 - learning_rate: 0.0010
Epoch 6/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6808 - loss: 0.6198 - val_accuracy: 0.6199 - val_loss: 1.9531 - learning_rate: 0.0010
Epoch 7/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7204 - loss: 0.

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6614 - loss: 0.6244 - val_accuracy: 0.6998 - val_loss: 0.7736 - learning_rate: 0.0010
Epoch 45/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7006 - loss: 0.5867 - val_accuracy: 0.4454 - val_loss: 2.3257 - learning_rate: 0.0010
Epoch 46/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.6700 - loss: 0.6028 - val_accuracy: 0.3801 - val_loss: 19.6861 - learning_rate: 0.0010
Epoch 47/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7146 - loss: 0.5748 - val_accuracy: 0.3817 - val_loss: 6.5864 - learning_rate: 0.0010
Epoch 48/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7295 - loss: 0.5572 - val_accuracy: 0.3883 - val_loss: 5.3554 - learning_rate: 0.0010
Epoch 49/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7075 - loss: 0.5795 - val_accuracy: 0.6199 - val_loss: 6.4512 - learning_rate: 0.0010
Epoch 50/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7017 - loss: 0.5978 -

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7183 - loss: 0.5802 - val_accuracy: 0.3801 - val_loss: 26.5257 - learning_rate: 0.0010
Epoch 88/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 25ms/step - accuracy: 0.7239 - loss: 0.5536 - val_accuracy: 0.6476 - val_loss: 1.6532 - learning_rate: 0.0010
Epoch 89/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.6975 - loss: 0.6034 - val_accuracy: 0.6346 - val_loss: 2.2074 - learning_rate: 0.0010
Epoch 90/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6886 - loss: 0.5991 - val_accuracy: 0.6199 - val_loss: 8.0043 - learning_rate: 0.0010
Epoch 91/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.6825 - loss: 0.6053 - val_accuracy: 0.7015 - val_loss: 0.7776 - learning_rate: 0.0010
Epoch 92/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7266 - loss: 0.5425 - val_accuracy: 0.7047 - val_loss: 0.6799 - learning_rate: 0.0010
Epoch 93/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6701 - loss: 0.6154 -

Epoch 130/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6959 - loss: 0.5870 - val_accuracy: 0.6542 - val_loss: 1.5135 - learning_rate: 5.0000e-04
Epoch 131/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7007 - loss: 0.6106 - val_accuracy: 0.5742 - val_loss: 1.0938 - learning_rate: 5.0000e-04
Epoch 132/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7348 - loss: 0.5464 - val_accuracy: 0.6101 - val_loss: 0.9651 - learning_rate: 5.0000e-04
Epoch 133/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7243 - loss: 0.5772 - val_accuracy: 0.3915 - val_loss: 4.2892 - learning_rate: 5.0000e-04
Epoch 134/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7002 - loss: 0.5808 - val_accuracy: 0.6199 - val_loss: 11.3025 - learning_rate: 5.0000e-04
Epoch 135/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7160 - loss: 0.5815 - val_accuracy: 0.3801 - val_loss: 10.8199 - learning_rate: 5.0000e-04
Epoch 136/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.7231 - loss: 0.5460 - val_accuracy: 0.6460 - val_loss: 1.8483 - learning_rate: 2.5000e-04
Epoch 173/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 28ms/step - accuracy: 0.7200 - loss: 0.5762 - val_accuracy: 0.6444 - val_loss: 1.8869 - learning_rate: 2.5000e-04
Epoch 174/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accuracy: 0.7068 - loss: 0.5811 - val_accuracy: 0.6656 - val_loss: 1.1967 - learning_rate: 2.5000e-04
Epoch 175/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 27ms/step - accuracy: 0.6667 - loss: 0.5975 - val_accuracy: 0.6884 - val_loss: 0.8608 - learning_rate: 2.5000e-04
Epoch 176/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 29ms/step - accuracy: 0.7067 - loss: 0.5600 - val_accuracy: 0.7064 - val_loss: 0.7269 - learning_rate: 2.5000e-04
Epoch 177/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 30ms/step - accuracy: 0.6864 - loss: 0.5905 - val_accuracy: 0.3817 - val_loss: 7.1202 - learning_rate: 2.5000e-04
Epoch 178/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 26ms/step - accu

...

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7170 - loss: 0.5619 - val_accuracy: 0.6656 - val_loss: 0.8126 - learning_rate: 1.0000e-04
Epoch 1811/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7010 - loss: 0.5742 - val_accuracy: 0.6737 - val_loss: 1.0541 - learning_rate: 1.0000e-04
Epoch 1812/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7322 - loss: 0.5651 - val_accuracy: 0.6770 - val_loss: 0.9495 - learning_rate: 1.0000e-04
Epoch 1813/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6926 - loss: 0.5761 - val_accuracy: 0.6835 - val_loss: 0.8389 - learning_rate: 1.0000e-04
Epoch 1814/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7304 - loss: 0.5725 - val_accuracy: 0.7015 - val_loss: 0.7282 - learning_rate: 1.0000e-04
Epoch 1815/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7023 - loss: 0.5646 - val_accuracy: 0.7015 - val_loss: 0.7436 - learning_rate: 1.0000e-04
Epoch 1816/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7120 - loss: 0.5587 - val_accuracy: 0.6248 - val_loss: 0.9429 - learning_rate: 1.0000e-04
Epoch 1853/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6741 - loss: 0.5637 - val_accuracy: 0.6819 - val_loss: 1.0121 - learning_rate: 1.0000e-04
Epoch 1854/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7426 - loss: 0.5465 - val_accuracy: 0.6639 - val_loss: 0.7993 - learning_rate: 1.0000e-04
Epoch 1855/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6875 - loss: 0.5707 - val_accuracy: 0.5824 - val_loss: 1.0606 - learning_rate: 1.0000e-04
Epoch 1856/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6773 - loss: 0.5826 - val_accuracy: 0.6933 - val_loss: 0.8021 - learning_rate: 1.0000e-04
Epoch 1857/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7303 - loss: 0.5450 - val_accuracy: 0.7015 - val_loss: 0.7521 - learning_rate: 1.0000e-04
Epoch 1858/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7385 - loss: 0.5442 - val_accuracy: 0.6623 - val_loss: 1.3372 - learning_rate: 1.0000e-04
Epoch 1895/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7038 - loss: 0.5601 - val_accuracy: 0.6835 - val_loss: 0.8617 - learning_rate: 1.0000e-04
Epoch 1896/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7180 - loss: 0.5636 - val_accuracy: 0.6819 - val_loss: 0.7618 - learning_rate: 1.0000e-04
Epoch 1897/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.6816 - loss: 0.5862 - val_accuracy: 0.7080 - val_loss: 0.7178 - learning_rate: 1.0000e-04
Epoch 1898/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 22ms/step - accuracy: 0.6998 - loss: 0.5691 - val_accuracy: 0.5889 - val_loss: 1.0132 - learning_rate: 1.0000e-04
Epoch 1899/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6811 - loss: 0.5722 - val_accuracy: 0.6933 - val_loss: 0.7711 - learning_rate: 1.0000e-04
Epoch 1900/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6990 - loss: 0.5589 - val_accuracy: 0.7080 - val_loss: 0.7395 - learning_rate: 1.0000e-04
Epoch 1937/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7134 - loss: 0.5739 - val_accuracy: 0.6835 - val_loss: 0.8243 - learning_rate: 1.0000e-04
Epoch 1938/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7031 - loss: 0.5649 - val_accuracy: 0.7113 - val_loss: 0.7248 - learning_rate: 1.0000e-04
Epoch 1939/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7610 - loss: 0.5478 - val_accuracy: 0.6656 - val_loss: 0.8298 - learning_rate: 1.0000e-04
Epoch 1940/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6991 - loss: 0.5924 - val_accuracy: 0.7096 - val_loss: 0.7262 - learning_rate: 1.0000e-04
Epoch 1941/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7320 - loss: 0.5405 - val_accuracy: 0.7031 - val_loss: 0.7483 - learning_rate: 1.0000e-04
Epoch 1942/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step 

37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7572 - loss: 0.5305 - val_accuracy: 0.6998 - val_loss: 0.7887 - learning_rate: 1.0000e-04
Epoch 1979/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.7117 - loss: 0.5774 - val_accuracy: 0.6803 - val_loss: 0.8977 - learning_rate: 1.0000e-04
Epoch 1980/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6942 - loss: 0.6045 - val_accuracy: 0.6786 - val_loss: 0.9770 - learning_rate: 1.0000e-04
Epoch 1981/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 21ms/step - accuracy: 0.7099 - loss: 0.5766 - val_accuracy: 0.6639 - val_loss: 1.2012 - learning_rate: 1.0000e-04
Epoch 1982/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 19ms/step - accuracy: 0.6926 - loss: 0.5692 - val_accuracy: 0.6770 - val_loss: 0.9865 - learning_rate: 1.0000e-04
Epoch 1983/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step - accuracy: 0.6749 - loss: 0.6161 - val_accuracy: 0.7064 - val_loss: 0.7271 - learning_rate: 1.0000e-04
Epoch 1984/2000
37/37 ━━━━━━━━━━━━━━━━━━━━ 1s 20ms/step 

In [18]:
def performance_j(list_1,list_2,int_a,int_b):
    m1 = min(list_1[int_a:int_b])
    m2 = min(list_2[int_a:int_b])
    
    ave_1 = sum(list_1[int_a:int_b])/len(list_1[int_a:int_b])
    ave_2 = sum(list_2[int_a:int_b])/len(list_2[int_a:int_b])
    
    sd_1 = np.sqrt(sum((x-ave_1)**2 for x in list_1[int_a:int_b])/len(list_1[int_a:int_b]))
    sd_2 = np.sqrt(sum((x-ave_2)**2 for x in list_2[int_a:int_b])/len(list_2[int_a:int_b]))
        
    if (ave_1-sd_1)<(ave_2-sd_2): 
        return [(ave_1-sd_1),(ave_2-sd_2),(ave_1-sd_1)]
    else:
        return [(ave_1-sd_1),(ave_2-sd_2),(ave_2-sd_2)]

In [19]:
def performance_k(list_1,list_2,int_a,int_b):
    m1 = min(list_1[int_a:int_b])
    m2 = min(list_2[int_a:int_b])
    
    ave_1 = sum(list_1[int_a:int_b])/len(list_1[int_a:int_b])
    ave_2 = sum(list_2[int_a:int_b])/len(list_2[int_a:int_b])
    
    sd_1 = np.sqrt(sum((x-ave_1)**2 for x in list_1[int_a:int_b])/len(list_1[int_a:int_b]))
    sd_2 = np.sqrt(sum((x-ave_2)**2 for x in list_2[int_a:int_b])/len(list_2[int_a:int_b]))
        
    if (ave_1-sd_1)<(ave_2-sd_2): 
        return [m1,m2,min(m1,m2)]
    else:
        return [m1,m2,min(m1,m2)]

In [20]:
perf1=[]
perf2=[]
perf3=[]
perf4=[]
perf5=[]
perf6=[]
perf7=[]
perf8=[]
perf9=[]
perf10=[]
perf11=[]
perf12=[]
perf13=[]
perf14=[]
perf15=[]
perf16=[]

for i in range(5):
    a1=performance_j(hist1.history['accuracy'],hist1.history['val_accuracy'],1500+i*100,1600+i*100)
    a2=performance_j(hist2.history['accuracy'],hist2.history['val_accuracy'],1500+i*100,1600+i*100)
    a3=performance_j(hist3.history['accuracy'],hist3.history['val_accuracy'],1500+i*100,1600+i*100)
    a4=performance_j(hist4.history['accuracy'],hist4.history['val_accuracy'],1500+i*100,1600+i*100)
    a5=performance_j(hist5.history['accuracy'],hist5.history['val_accuracy'],1500+i*100,1600+i*100)
    a6=performance_j(hist6.history['accuracy'],hist6.history['val_accuracy'],1500+i*100,1600+i*100)
    a7=performance_j(hist7.history['accuracy'],hist7.history['val_accuracy'],1500+i*100,1600+i*100)
    a8=performance_j(hist8.history['accuracy'],hist8.history['val_accuracy'],1500+i*100,1600+i*100)
    a9=performance_j(hist9.history['accuracy'],hist9.history['val_accuracy'],1500+i*100,1600+i*100)
    a10=performance_j(hist10.history['accuracy'],hist10.history['val_accuracy'],1500+i*100,1600+i*100)
    a11=performance_j(hist11.history['accuracy'],hist11.history['val_accuracy'],1500+i*100,1600+i*100)
    a12=performance_j(hist12.history['accuracy'],hist12.history['val_accuracy'],1500+i*100,1600+i*100)
    a13=performance_j(hist13.history['accuracy'],hist13.history['val_accuracy'],1500+i*100,1600+i*100)
    a14=performance_j(hist14.history['accuracy'],hist14.history['val_accuracy'],1500+i*100,1600+i*100)
    a15=performance_j(hist15.history['accuracy'],hist15.history['val_accuracy'],1500+i*100,1600+i*100)
    a16=performance_j(hist16.history['accuracy'],hist16.history['val_accuracy'],1500+i*100,1600+i*100)

    perf1 = perf1+a1
    perf2 = perf2+a2
    perf3 = perf3+a3
    perf4 = perf4+a4
    perf5 = perf5+a5
    perf6 = perf6+a6
    perf7 = perf7+a7
    perf8 = perf8+a8
    perf9 = perf9+a9
    perf10 = perf10+a10
    perf11 = perf11+a11
    perf12 = perf12+a12
    perf13 = perf13+a13
    perf14 = perf14+a14
    perf15 = perf15+a15
    perf16 = perf16+a16
    
PERF=[perf1,perf2,perf3,perf4,perf5,perf6,perf7,perf8,perf9,
perf10,perf11,perf12,perf13,perf14,perf15,perf16]   

dataframe =pd.DataFrame(PERF)
dataframe.to_csv("fcn_perf_j_trial6.csv",header=False,index=False)

In [21]:
perf1=[]
perf2=[]
perf3=[]
perf4=[]
perf5=[]
perf6=[]
perf7=[]
perf8=[]
perf9=[]
perf10=[]
perf11=[]
perf12=[]
perf13=[]
perf14=[]
perf15=[]
perf16=[]

for i in range(5):
    a1=performance_k(hist1.history['accuracy'],hist1.history['val_accuracy'],1500+i*100,1600+i*100)
    a2=performance_k(hist2.history['accuracy'],hist2.history['val_accuracy'],1500+i*100,1600+i*100)
    a3=performance_k(hist3.history['accuracy'],hist3.history['val_accuracy'],1500+i*100,1600+i*100)
    a4=performance_k(hist4.history['accuracy'],hist4.history['val_accuracy'],1500+i*100,1600+i*100)
    a5=performance_k(hist5.history['accuracy'],hist5.history['val_accuracy'],1500+i*100,1600+i*100)
    a6=performance_k(hist6.history['accuracy'],hist6.history['val_accuracy'],1500+i*100,1600+i*100)
    a7=performance_k(hist7.history['accuracy'],hist7.history['val_accuracy'],1500+i*100,1600+i*100)
    a8=performance_k(hist8.history['accuracy'],hist8.history['val_accuracy'],1500+i*100,1600+i*100)
    a9=performance_k(hist9.history['accuracy'],hist9.history['val_accuracy'],1500+i*100,1600+i*100)
    a10=performance_k(hist10.history['accuracy'],hist10.history['val_accuracy'],1500+i*100,1600+i*100)
    a11=performance_k(hist11.history['accuracy'],hist11.history['val_accuracy'],1500+i*100,1600+i*100)
    a12=performance_k(hist12.history['accuracy'],hist12.history['val_accuracy'],1500+i*100,1600+i*100)
    a13=performance_k(hist13.history['accuracy'],hist13.history['val_accuracy'],1500+i*100,1600+i*100)
    a14=performance_k(hist14.history['accuracy'],hist14.history['val_accuracy'],1500+i*100,1600+i*100)
    a15=performance_k(hist15.history['accuracy'],hist15.history['val_accuracy'],1500+i*100,1600+i*100)
    a16=performance_k(hist16.history['accuracy'],hist16.history['val_accuracy'],1500+i*100,1600+i*100)


    perf1 = perf1+a1
    perf2 = perf2+a2
    perf3 = perf3+a3
    perf4 = perf4+a4
    perf5 = perf5+a5
    perf6 = perf6+a6
    perf7 = perf7+a7
    perf8 = perf8+a8
    perf9 = perf9+a9
    perf10 = perf10+a10
    perf11 = perf11+a11
    perf12 = perf12+a12
    perf13 = perf13+a13
    perf14 = perf14+a14
    perf15 = perf15+a15
    perf16 = perf16+a16
    
PERF=[perf1,perf2,perf3,perf4,perf5,perf6,perf7,perf8,perf9,
perf10,perf11,perf12,perf13,perf14,perf15,perf16]   

dataframe =pd.DataFrame(PERF)
dataframe.to_csv("s&p500_fcn_perf_k_trial6.csv",header=False,index=False)

In [22]:
import csv

# Define the lists
tr1 = hist1.history['accuracy']
te1 = hist1.history['val_accuracy']
tr2 = hist2.history['accuracy']
te2 = hist2.history['val_accuracy']
tr3 = hist3.history['accuracy']
te3 = hist3.history['val_accuracy']
tr4 = hist4.history['accuracy']
te4 = hist4.history['val_accuracy']
tr5 = hist5.history['accuracy']
te5 = hist5.history['val_accuracy']
tr6 = hist6.history['accuracy']
te6 = hist6.history['val_accuracy']
tr7 = hist7.history['accuracy']
te7 = hist7.history['val_accuracy']
tr8 = hist8.history['accuracy']
te8 = hist8.history['val_accuracy']
tr9 = hist9.history['accuracy']
te9 = hist9.history['val_accuracy']
tr10 = hist10.history['accuracy']
te10 = hist10.history['val_accuracy']
tr11 = hist11.history['accuracy']
te11 = hist11.history['val_accuracy']
tr12 = hist12.history['accuracy']
te12 = hist12.history['val_accuracy']
tr13 = hist13.history['accuracy']
te13 = hist13.history['val_accuracy']
tr14 = hist14.history['accuracy']
te14 = hist14.history['val_accuracy']
tr15 = hist15.history['accuracy']
te15 = hist15.history['val_accuracy']
tr16 = hist16.history['accuracy']
te16 = hist16.history['val_accuracy']
# Specify the filename
filename = "s&p500_fcn_history_trial6.csv"

# Write to the CSV file
with open(filename, mode='w', newline='') as file:
    writer = csv.writer(file)
    
    # Write the header
    writer.writerow(['tr1', 'te1', 'tr2', 'te2', 'tr3', 'te3', 'tr4', 'te4', 'tr5', 'te5', 'tr6', 'te6', 'tr7', 'te7', 'tr8', 'te8', 'tr9', 'te9', 'tr10', 'te10', 'tr11', 'te11', 'tr12', 'te12', 'tr13', 'te13', 'tr14', 'te14', 'tr15', 'te15', 'tr16', 'te16'])
    
    # Write the data rows
    for a1,b1,a2,b2,a3,b3,a4,b4,a5,b5,a6,b6,a7,b7,a8,b8,a9,b9,a10,b10,a11,b11,a12,b12,a13,b13,a14,b14,a15,b15,a16,b16 in zip(tr1, te1, tr2, te2, tr3, te3, tr4, te4, tr5, te5, tr6, te6,
tr7, te7, tr8, te8, tr9, te9, tr10, te10, tr11, te11, tr12, te12,
tr13, te13, tr14, te14, tr15, te15, tr16, te16):
        writer.writerow([a1,b1,a2,b2,a3,b3,a4,b4,a5,b5,a6,b6,a7,b7,a8,b8,a9,b9,a10,b10,a11,b11,a12,b12,a13,b13,a14,b14,a15,b15,a16,b16])

print(f"Data successfully written to {filename}")

Data successfully written to s&p500_fcn_history_trial6.csv
